# IBM Capstone Assignment (Week 4 & 5)

<h5>Assume that i am a Real Estate Agent in Singapore assisting my Client Mr Edwin  to Find a HDB( Housing Development Board) Flat in Singapore</h5>

<h6> My Objective is to Propose 1 Flat at each  Location (Toa Payoh / Ang Mokio / Hougang ) For My Client to Decide Which He will go For to purchase </h6>

<h5>My Client Gave me a Stringent Expectation as below </h5>

<ol>
<li>
My client  looking for a 4 Room HDB Flat ( Can be Model A / ModelA2 / DBSS/ Simplified Etc)
    
</li>

<li>
Area that My Client looking at (Toa Payoh / Ang Mokio / Hougang)
</li>

<li>
Should Be Near by Train Station (MRT)
</li>

<li>
Should have HyperMart(Fair Price/ Giant / Cold Storage / Sheng Siong) Near By
</li>



<li>
Leasing Left Should be be more that t > 70 Years ( In Singapore Governement Build HDB Flat have a Leasing Years of 99 Years) 
    
</li>    


<li>
Slightly below Market  Rate Average Price
</li>


</ol>

<b>Import All Necessary Library</b>

In [1]:
from bs4 import BeautifulSoup 
import requests
import numpy as np
import pandas as pd
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from pandas.io.json import json_normalize  # tranform JSON file into a pandas dataframe

import folium # map rendering library

# import k-means from clustering stage
from sklearn.cluster import KMeans

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import json
import re

<b>Read HDB Flat Historical Price </b>

In [2]:

# The Below Enable to View All Rows  and Column
#pd.set_option('display.max_rows', None)
#pd.set_option('display.max_columns', None)
#pd.set_option('display.width', None)

#The CSV File copy form data.gov.sg

url = 'https://raw.githubusercontent.com/khaiseng82/hdb-/main/resale-flat-prices-based-on-registration-date-from-jan-2017-onwards.csv'
df_Origin = pd.read_csv(url, index_col=0)

df_Origin

town  flat_type block        street_name storey_range  \
month                                                                  
2017-01  ANG MO KIO     2 ROOM   406  ANG MO KIO AVE 10     10 TO 12   
2017-01  ANG MO KIO     3 ROOM   108   ANG MO KIO AVE 4     01 TO 03   
2017-01  ANG MO KIO     3 ROOM   602   ANG MO KIO AVE 5     01 TO 03   
2017-01  ANG MO KIO     3 ROOM   465  ANG MO KIO AVE 10     04 TO 06   
2017-01  ANG MO KIO     3 ROOM   601   ANG MO KIO AVE 5     01 TO 03   
...             ...        ...   ...                ...          ...   
2021-04      YISHUN  EXECUTIVE   326     YISHUN RING RD     10 TO 12   
2021-04      YISHUN  EXECUTIVE   360     YISHUN RING RD     04 TO 06   
2021-04      YISHUN  EXECUTIVE   326     YISHUN RING RD     10 TO 12   
2021-04      YISHUN  EXECUTIVE   355     YISHUN RING RD     10 TO 12   
2021-04      YISHUN  EXECUTIVE   277       YISHUN ST 22     04 TO 06   

         floor_area_sqm      flat_model  lease_commence_date  \
month                                                          
2017-01            44.0        Improved                 1979   
2017-01            67.0  New Generation                 1978   
2017-01            67.0  New Generation                 1980   
2017-01            68.0  New Generation                 1980   
2017-01            67.0  New Generation                 1980   
...                 ...             ...                  ...   
2021-04           146.0      Maisonette                 1988   
2021-04           146.0      Maisonette                 1988   
2021-04           146.0      Maisonette                 1988   
2021-04           146.0      Maisonette                 1988   
2021-04           146.0      Maisonette                 1985   

            remaining_lease  resale_price  
month                                      
2017-01  61 years 04 months      232000.0  
2017-01  60 years 07 months      250000.0  
2017-01  62 years 05 months      262000.0  
2017-01   62 years 01 month      265000.0  
2017-01  62 years 05 months      265000.0  
...                     ...           ...  
2021-04  66 years 04 months      650000.0  
2021-04  66 years 04 months      645000.0  
2021-04  66 years 04 months      585000.0  
2021-04  66 years 08 months      675000.0  
2021-04  63 years 05 months      625000.0  

[95858 rows x 10 columns]

In [3]:
# Check how many Rows and Column
df_Origin.shape


(95858, 10)

<b>Now Need to Extract the Data According to the Criteria as Below</b>

<ol>
<li>
Contain only 3 Area town :( Toa Payoh/ Ang Mo kio / Hougang)
</li>
<li>
History Price should be 2021 and beyond
</li>
<li>
flat_type should be 4 Room
</li>
<li>
Lease Year Should be 70 Years and above
</li>

</ol>

3 Area town :( Toa Payoh/ Ang Mo kio / Hougang)

In [4]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)


    
df_3_town =df_Origin[df_Origin['town'].str.contains('ANG MO KIO|TOA PAYOH|HOUGANG',case=False, regex=True)].reset_index(drop=False)
df_3_town

month        town  flat_type block         street_name storey_range  \
0      2017-01  ANG MO KIO     2 ROOM   406   ANG MO KIO AVE 10     10 TO 12   
1      2017-01  ANG MO KIO     3 ROOM   108    ANG MO KIO AVE 4     01 TO 03   
2      2017-01  ANG MO KIO     3 ROOM   602    ANG MO KIO AVE 5     01 TO 03   
3      2017-01  ANG MO KIO     3 ROOM   465   ANG MO KIO AVE 10     04 TO 06   
4      2017-01  ANG MO KIO     3 ROOM   601    ANG MO KIO AVE 5     01 TO 03   
5      2017-01  ANG MO KIO     3 ROOM   150    ANG MO KIO AVE 5     01 TO 03   
6      2017-01  ANG MO KIO     3 ROOM   447   ANG MO KIO AVE 10     04 TO 06   
7      2017-01  ANG MO KIO     3 ROOM   218    ANG MO KIO AVE 1     04 TO 06   
8      2017-01  ANG MO KIO     3 ROOM   447   ANG MO KIO AVE 10     04 TO 06   
9      2017-01  ANG MO KIO     3 ROOM   571    ANG MO KIO AVE 3     01 TO 03   
10     2017-01  ANG MO KIO     3 ROOM   534   ANG MO KIO AVE 10     01 TO 03   
11     2017-01  ANG MO KIO     3 ROOM   233    ANG MO KIO AVE 3     10 TO 12   
12     2017-01  ANG MO KIO     3 ROOM   235    ANG MO KIO AVE 3     04 TO 06   
13     2017-01  ANG MO KIO     3 ROOM   219    ANG MO KIO AVE 1     07 TO 09   
14     2017-01  ANG MO KIO     3 ROOM   536   ANG MO KIO AVE 10     07 TO 09   
15     2017-01  ANG MO KIO     3 ROOM   230    ANG MO KIO AVE 3     04 TO 06   
16     2017-01  ANG MO KIO     3 ROOM   570    ANG MO KIO AVE 3     10 TO 12   
17     2017-01  ANG MO KIO     3 ROOM   624    ANG MO KIO AVE 4     04 TO 06   
18     2017-01  ANG MO KIO     3 ROOM   441   ANG MO KIO AVE 10     07 TO 09   
19     2017-01  ANG MO KIO     3 ROOM   625    ANG MO KIO AVE 9     04 TO 06   
20     2017-01  ANG MO KIO     3 ROOM   119    ANG MO KIO AVE 3     07 TO 09   
21     2017-01  ANG MO KIO     3 ROOM   255    ANG MO KIO AVE 4     04 TO 06   
22     2017-01  ANG MO KIO     3 ROOM   432   ANG MO KIO AVE 10     10 TO 12   
23     2017-01  ANG MO KIO     3 ROOM   211    ANG MO KIO AVE 3     01 TO 03   
24     2017-01  ANG MO KIO     3 ROOM   584    ANG MO KIO AVE 3     04 TO 06   
25     2017-01  ANG MO KIO     3 ROOM   118    ANG MO KIO AVE 4     07 TO 09   
26     2017-01  ANG MO KIO     3 ROOM   333    ANG MO KIO AVE 1     07 TO 09   
27     2017-01  ANG MO KIO     3 ROOM   256    ANG MO KIO AVE 4     10 TO 12   
28     2017-01  ANG MO KIO     3 ROOM   330    ANG MO KIO AVE 1     07 TO 09   
29     2017-01  ANG MO KIO     3 ROOM   557   ANG MO KIO AVE 10     10 TO 12   
30     2017-01  ANG MO KIO     3 ROOM   302    ANG MO KIO AVE 3     10 TO 12   
31     2017-01  ANG MO KIO     3 ROOM   575   ANG MO KIO AVE 10     07 TO 09   
32     2017-01  ANG MO KIO     3 ROOM   509    ANG MO KIO AVE 8     01 TO 03   
33     2017-01  ANG MO KIO     4 ROOM   472   ANG MO KIO AVE 10     10 TO 12   
34     2017-01  ANG MO KIO     4 ROOM   475   ANG MO KIO AVE 10     07 TO 09   
35     2017-01  ANG MO KIO     4 ROOM   629    ANG MO KIO AVE 4     01 TO 03   
36     2017-01  ANG MO KIO     4 ROOM   546   ANG MO KIO AVE 10     01 TO 03   
37     2017-01  ANG MO KIO     4 ROOM   131    ANG MO KIO AVE 3     01 TO 03   
38     2017-01  ANG MO KIO     4 ROOM   254    ANG MO KIO AVE 4     04 TO 06   
39     2017-01  ANG MO KIO     4 ROOM   470   ANG MO KIO AVE 10     04 TO 06   
40     2017-01  ANG MO KIO     4 ROOM   601    ANG MO KIO AVE 5     04 TO 06   
41     2017-01  ANG MO KIO     4 ROOM   463   ANG MO KIO AVE 10     04 TO 06   
42     2017-01  ANG MO KIO     4 ROOM   207    ANG MO KIO AVE 1     04 TO 06   
43     2017-01  ANG MO KIO     4 ROOM   304    ANG MO KIO AVE 1     10 TO 12   
44     2017-01  ANG MO KIO     4 ROOM   646    ANG MO KIO AVE 6     10 TO 12   
45     2017-01  ANG MO KIO     4 ROOM   328    ANG MO KIO AVE 3     10 TO 12   
46     2017-01  ANG MO KIO     4 ROOM  588C    ANG MO KIO ST 52     13 TO 15   
47     2017-01  ANG MO KIO     4 ROOM  588D    ANG MO KIO ST 52     19 TO 21   
48     2017-01  ANG MO KIO     4 ROOM  588D    ANG MO KIO ST 52     22 TO 24   
49     20

In [5]:
df_3_town.shape

(12017, 11)

<b>Flat_type should be 4 Room</b>

In [6]:
df_3_town_4R = df_3_town[df_3_town['flat_type'].str.contains("4 ROOM")].reset_index(drop=True)
df_3_town_4R.head()

month        town flat_type block        street_name storey_range  \
0  2017-01  ANG MO KIO    4 ROOM   472  ANG MO KIO AVE 10     10 TO 12   
1  2017-01  ANG MO KIO    4 ROOM   475  ANG MO KIO AVE 10     07 TO 09   
2  2017-01  ANG MO KIO    4 ROOM   629   ANG MO KIO AVE 4     01 TO 03   
3  2017-01  ANG MO KIO    4 ROOM   546  ANG MO KIO AVE 10     01 TO 03   
4  2017-01  ANG MO KIO    4 ROOM   131   ANG MO KIO AVE 3     01 TO 03   

   floor_area_sqm      flat_model  lease_commence_date     remaining_lease  \
0            92.0  New Generation                 1979  61 years 06 months   
1            91.0  New Generation                 1979  61 years 06 months   
2            94.0  New Generation                 1981  63 years 09 months   
3            92.0  New Generation                 1981            63 years   
4            98.0  New Generation                 1979   61 years 01 month   

   resale_price  
0      400000.0  
1      400000.0  
2      403000.0  
3      410000.0  
4      425888.0

In [7]:
df_3_town_4R.shape

(4137, 11)

<b>Get the Latest Price at Year 2021</b>

In [8]:
df_3_town_4R_21 =df_3_town_4R.loc[df_3_town_4R["month"]>="2021-01"]

In [9]:
df_3_town_4R_21.head()

month        town flat_type block        street_name storey_range  \
3771  2021-01  ANG MO KIO    4 ROOM   305   ANG MO KIO AVE 1     07 TO 09   
3772  2021-01  ANG MO KIO    4 ROOM   413  ANG MO KIO AVE 10     10 TO 12   
3773  2021-01  ANG MO KIO    4 ROOM   414  ANG MO KIO AVE 10     01 TO 03   
3774  2021-01  ANG MO KIO    4 ROOM   415  ANG MO KIO AVE 10     07 TO 09   
3775  2021-01  ANG MO KIO    4 ROOM   547  ANG MO KIO AVE 10     04 TO 06   

      floor_area_sqm      flat_model  lease_commence_date     remaining_lease  \
3771            97.0  New Generation                 1977  55 years 06 months   
3772            92.0  New Generation                 1979  57 years 08 months   
3773            92.0  New Generation                 1979  57 years 09 months   
3774            92.0  New Generation                 1979  57 years 08 months   
3775            92.0  New Generation                 1981            59 years   

      resale_price  
3771      448000.0  
3772      420000.0  
3773      375000.0  
3774      420000.0  
3775      370000.0

In [10]:
df_3_town_4R_21.shape

(366, 11)

<b>Drop the Remaining Lease Column ( Will Recalculate and append a new Column Later)</b>

In [11]:
df_3_town_4R_21=df_3_town_4R_21.drop(['remaining_lease'], axis=1)

In [12]:
df_3_town_4R_21.head()

month        town flat_type block        street_name storey_range  \
3771  2021-01  ANG MO KIO    4 ROOM   305   ANG MO KIO AVE 1     07 TO 09   
3772  2021-01  ANG MO KIO    4 ROOM   413  ANG MO KIO AVE 10     10 TO 12   
3773  2021-01  ANG MO KIO    4 ROOM   414  ANG MO KIO AVE 10     01 TO 03   
3774  2021-01  ANG MO KIO    4 ROOM   415  ANG MO KIO AVE 10     07 TO 09   
3775  2021-01  ANG MO KIO    4 ROOM   547  ANG MO KIO AVE 10     04 TO 06   

      floor_area_sqm      flat_model  lease_commence_date  resale_price  
3771            97.0  New Generation                 1977      448000.0  
3772            92.0  New Generation                 1979      420000.0  
3773            92.0  New Generation                 1979      375000.0  
3774            92.0  New Generation                 1979      420000.0  
3775            92.0  New Generation                 1981      370000.0

<b>Calculate Lease Remaining  and Add a New 'remain_lease' Column</b>

In [13]:
df_3_town_4R_21['remain_lease'] = 99-(2021 - df_3_town_4R_21['lease_commence_date'])

In [14]:
df_3_town_4R_21.head()

month        town flat_type block        street_name storey_range  \
3771  2021-01  ANG MO KIO    4 ROOM   305   ANG MO KIO AVE 1     07 TO 09   
3772  2021-01  ANG MO KIO    4 ROOM   413  ANG MO KIO AVE 10     10 TO 12   
3773  2021-01  ANG MO KIO    4 ROOM   414  ANG MO KIO AVE 10     01 TO 03   
3774  2021-01  ANG MO KIO    4 ROOM   415  ANG MO KIO AVE 10     07 TO 09   
3775  2021-01  ANG MO KIO    4 ROOM   547  ANG MO KIO AVE 10     04 TO 06   

      floor_area_sqm      flat_model  lease_commence_date  resale_price  \
3771            97.0  New Generation                 1977      448000.0   
3772            92.0  New Generation                 1979      420000.0   
3773            92.0  New Generation                 1979      375000.0   
3774            92.0  New Generation                 1979      420000.0   
3775            92.0  New Generation                 1981      370000.0   

      remain_lease  
3771            55  
3772            57  
3773            57  
3774            57  
3775            59

<b>Re order the Remain lease Column  to behind lease_commence_date</b>

In [15]:
df_3_town_4R_21 = df_3_town_4R_21[["month", "town", "flat_type","block","street_name","storey_range","floor_area_sqm","flat_model","lease_commence_date","remain_lease","resale_price"]]

In [16]:
df_3_town_4R_21.head()

month        town flat_type block        street_name storey_range  \
3771  2021-01  ANG MO KIO    4 ROOM   305   ANG MO KIO AVE 1     07 TO 09   
3772  2021-01  ANG MO KIO    4 ROOM   413  ANG MO KIO AVE 10     10 TO 12   
3773  2021-01  ANG MO KIO    4 ROOM   414  ANG MO KIO AVE 10     01 TO 03   
3774  2021-01  ANG MO KIO    4 ROOM   415  ANG MO KIO AVE 10     07 TO 09   
3775  2021-01  ANG MO KIO    4 ROOM   547  ANG MO KIO AVE 10     04 TO 06   

      floor_area_sqm      flat_model  lease_commence_date  remain_lease  \
3771            97.0  New Generation                 1977            55   
3772            92.0  New Generation                 1979            57   
3773            92.0  New Generation                 1979            57   
3774            92.0  New Generation                 1979            57   
3775            92.0  New Generation                 1981            59   

      resale_price  
3771      448000.0  
3772      420000.0  
3773      375000.0  
3774      420000.0  
3775      370000.0

<b>Get Lease Remaining More than or equal to 70 Years</b>

In [17]:
#pd.set_option('display.max_rows', None)
#pd.set_option('display.max_columns', None)
#pd.set_option('display.width', None)

df_filtered = df_3_town_4R_21[df_3_town_4R_21['remain_lease']>=70]
df_filtered.head() 

month        town flat_type block       street_name storey_range  \
3784  2021-01  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     01 TO 03   
3786  2021-01  ANG MO KIO    4 ROOM  700B  ANG MO KIO AVE 6     22 TO 24   
3788  2021-01  ANG MO KIO    4 ROOM  700C  ANG MO KIO AVE 6     13 TO 15   
3790  2021-01  ANG MO KIO    4 ROOM  315A  ANG MO KIO ST 31     04 TO 06   
3791  2021-01  ANG MO KIO    4 ROOM  309A  ANG MO KIO ST 31     04 TO 06   

      floor_area_sqm flat_model  lease_commence_date  remain_lease  \
3784           107.0    Model A                 1996            74   
3786            90.0    Model A                 2003            81   
3788            85.0    Model A                 2003            81   
3790            90.0    Model A                 2006            84   
3791            90.0    Model A                 2006            84   

      resale_price  
3784      508000.0  
3786      690000.0  
3788      665000.0  
3790      580000.0  
3791      505055.0

In [18]:
df_filtered.shape

(183, 11)

<b>Sort By "town"</b>

In [19]:
df_filtered_sorted=df_filtered.sort_values(by=['town'])
df_filtered_sorted.reset_index(drop=True, inplace=True)
df_filtered_sorted.head()

month        town flat_type block       street_name storey_range  \
0  2021-01  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     01 TO 03   
1  2021-04  ANG MO KIO    4 ROOM  588D  ANG MO KIO ST 52     16 TO 18   
2  2021-02  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     13 TO 15   
3  2021-02  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     22 TO 24   
4  2021-02  ANG MO KIO    4 ROOM  596C  ANG MO KIO ST 52     22 TO 24   

   floor_area_sqm flat_model  lease_commence_date  remain_lease  resale_price  
0           107.0    Model A                 1996            74      508000.0  
1            91.0       DBSS                 2011            89      770000.0  
2            91.0    Model A                 2002            80      665000.0  
3            90.0       DBSS                 2011            89      768000.0  
4            90.0    Model A                 2002            80      680888.0

<h2>Now we have Clean Up and Extract the Data we need to Analyze Next Step is to Get the Coordinate( Longtitude, Latitude) for the Flat Unit to be Append to the Dataframe </H2>

<b>Combine Block Number and Street Name  to Form an Address</b>

In [20]:
df_filtered_sorted['address'] = df_filtered_sorted['block'] + " " + df_filtered_sorted['street_name']
# Dedup Address List
df_dedup = df_filtered_sorted.drop_duplicates(subset='address', keep='first')
len(df_dedup)
df_dedup.head() 

month        town flat_type block       street_name storey_range  \
0  2021-01  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     01 TO 03   
1  2021-04  ANG MO KIO    4 ROOM  588D  ANG MO KIO ST 52     16 TO 18   
2  2021-02  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     13 TO 15   
3  2021-02  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     22 TO 24   
4  2021-02  ANG MO KIO    4 ROOM  596C  ANG MO KIO ST 52     22 TO 24   

   floor_area_sqm flat_model  lease_commence_date  remain_lease  resale_price  \
0           107.0    Model A                 1996            74      508000.0   
1            91.0       DBSS                 2011            89      770000.0   
2            91.0    Model A                 2002            80      665000.0   
3            90.0       DBSS                 2011            89      768000.0   
4            90.0    Model A                 2002            80      680888.0   

                 address  
0   619 ANG MO KIO AVE 4  
1  588D ANG MO KIO ST 52  
2  596A ANG MO KIO ST 52  
3  588B ANG MO KIO ST 52  
4  596C ANG MO KIO ST 52

<b> Before Convert to List</b>

In [21]:
df_dedup['address']

0         619 ANG MO KIO AVE 4
1        588D ANG MO KIO ST 52
2        596A ANG MO KIO ST 52
3        588B ANG MO KIO ST 52
4        596C ANG MO KIO ST 52
5        308A ANG MO KIO AVE 1
6        307A ANG MO KIO AVE 1
7        307B ANG MO KIO AVE 1
10        353 ANG MO KIO ST 32
12       596B ANG MO KIO ST 52
16        351 ANG MO KIO ST 32
17       315A ANG MO KIO ST 31
18       309A ANG MO KIO ST 31
20       700C ANG MO KIO AVE 6
21       700B ANG MO KIO AVE 6
22       316A ANG MO KIO ST 31
23       307C ANG MO KIO AVE 1
24          984A BUANGKOK LINK
25         988A BUANGKOK GREEN
26          985A BUANGKOK CRES
27           165 HOUGANG AVE 1
28           169 HOUGANG AVE 1
29           917 HOUGANG AVE 9
30            838 HOUGANG CTRL
31     476B UPP SERANGOON VIEW
33     476C UPP SERANGOON VIEW
35     477C UPP SERANGOON VIEW
36         988C BUANGKOK GREEN
37          978C BUANGKOK CRES
38         987C BUANGKOK GREEN
41     477B UPP SERANGOON VIEW
43     470B UPP SERANGOON CRES
44     4

<b>Convert it to List to Prepare for FOR Loop</b>

In [22]:
address_list = df_dedup['address'].tolist()
len(address_list)
address_list

['619 ANG MO KIO AVE 4',
 '588D ANG MO KIO ST 52',
 '596A ANG MO KIO ST 52',
 '588B ANG MO KIO ST 52',
 '596C ANG MO KIO ST 52',
 '308A ANG MO KIO AVE 1',
 '307A ANG MO KIO AVE 1',
 '307B ANG MO KIO AVE 1',
 '353 ANG MO KIO ST 32',
 '596B ANG MO KIO ST 52',
 '351 ANG MO KIO ST 32',
 '315A ANG MO KIO ST 31',
 '309A ANG MO KIO ST 31',
 '700C ANG MO KIO AVE 6',
 '700B ANG MO KIO AVE 6',
 '316A ANG MO KIO ST 31',
 '307C ANG MO KIO AVE 1',
 '984A BUANGKOK LINK',
 '988A BUANGKOK GREEN',
 '985A BUANGKOK CRES',
 '165 HOUGANG AVE 1',
 '169 HOUGANG AVE 1',
 '917 HOUGANG AVE 9',
 '838 HOUGANG CTRL',
 '476B UPP SERANGOON VIEW',
 '476C UPP SERANGOON VIEW',
 '477C UPP SERANGOON VIEW',
 '988C BUANGKOK GREEN',
 '978C BUANGKOK CRES',
 '987C BUANGKOK GREEN',
 '477B UPP SERANGOON VIEW',
 '470B UPP SERANGOON CRES',
 '475D UPP SERANGOON CRES',
 '473B UPP SERANGOON CRES',
 '470A UPP SERANGOON CRES',
 '475A UPP SERANGOON CRES',
 '939 HOUGANG ST 92',
 '915 HOUGANG ST 91',
 '926 HOUGANG ST 91',
 '911 HOUGANG S

<b>Now We have the Address will Use OneMap Api to get Coordinate </b>

In [23]:

# Declare eMpty List
latitude = []
longitude = []
blk_no = []
road_name = []
postal_code = []
address = []
count = 0

for row in range(len(address_list)):
    #formulate query string  
    query_address = address_list[row]
    # Query the API
    query_string='https://developers.onemap.sg/commonapi/search?searchVal='+str(query_address)+'&returnGeom=Y&getAddrDetails=Y'
    resp = requests.get(query_string)          

    #Convert JSON into Python Object
    data_geo_location=json.loads(resp.content)
    if data_geo_location['found'] != 0:
        latitude.append(data_geo_location['results'][0]['LATITUDE'])
        longitude.append(data_geo_location['results'][0]['LONGITUDE'])
        blk_no.append(data_geo_location['results'][0]['BLK_NO'])
        road_name.append(data_geo_location['results'][0]['ROAD_NAME'])
        postal_code.append(data_geo_location['results'][0]['POSTAL'])
        address.append(query_address)
        print (str(query_address) + " ,Lat: " + data_geo_location['results'][0]['LATITUDE'] + " Long: " + data_geo_location['results'][0]['LONGITUDE'])
    else:
        print ("No Results")

619 ANG MO KIO AVE 4 ,Lat: 1.3785880768512 Long: 103.838639699065
588D ANG MO KIO ST 52 ,Lat: 1.37175400663025 Long: 103.8538833087
596A ANG MO KIO ST 52 ,Lat: 1.37243023974421 Long: 103.850949173949
588B ANG MO KIO ST 52 ,Lat: 1.37197571261128 Long: 103.853150894936
596C ANG MO KIO ST 52 ,Lat: 1.37193571932412 Long: 103.85014325987
308A ANG MO KIO AVE 1 ,Lat: 1.36548342757104 Long: 103.844084739929
307A ANG MO KIO AVE 1 ,Lat: 1.36598205054585 Long: 103.84444497466
307B ANG MO KIO AVE 1 ,Lat: 1.36583937026387 Long: 103.844630828457
353 ANG MO KIO ST 32 ,Lat: 1.36406807879641 Long: 103.851612284582
596B ANG MO KIO ST 52 ,Lat: 1.37205123278789 Long: 103.850545847531
351 ANG MO KIO ST 32 ,Lat: 1.36432366673954 Long: 103.850307632579
315A ANG MO KIO ST 31 ,Lat: 1.36421831526448 Long: 103.846861474806
309A ANG MO KIO ST 31 ,Lat: 1.36502933267756 Long: 103.845300649183
700C ANG MO KIO AVE 6 ,Lat: 1.36944159368432 Long: 103.84648823913
700B ANG MO KIO AVE 6 ,Lat: 1.36941049804616 Long: 103.84

<b>Fit Query Result into DataFrame </b>

In [24]:
# Fit into a dataframe
df_coordinates = pd.DataFrame({
    'latitude': latitude,
    'longitude': longitude,
    'blk_no': blk_no,
    'road_name': road_name,
    'postal_code': postal_code,
    'address': address
})

In [25]:
df_coordinates

latitude         longitude blk_no                 road_name  \
0     1.3785880768512  103.838639699065    619       ANG MO KIO AVENUE 4   
1    1.37175400663025    103.8538833087   588D      ANG MO KIO STREET 52   
2    1.37243023974421  103.850949173949   596A      ANG MO KIO STREET 52   
3    1.37197571261128  103.853150894936   588B      ANG MO KIO STREET 52   
4    1.37193571932412   103.85014325987   596C      ANG MO KIO STREET 52   
5    1.36548342757104  103.844084739929   308A       ANG MO KIO AVENUE 1   
6    1.36598205054585   103.84444497466   307A       ANG MO KIO AVENUE 1   
7    1.36583937026387  103.844630828457   307B       ANG MO KIO AVENUE 1   
8    1.36406807879641  103.851612284582    353      ANG MO KIO STREET 32   
9    1.37205123278789  103.850545847531   596B      ANG MO KIO STREET 52   
10   1.36432366673954  103.850307632579    351      ANG MO KIO STREET 32   
11   1.36421831526448  103.846861474806   315A      ANG MO KIO STREET 31   
12   1.36502933267756  103.845300649183   309A      ANG MO KIO STREET 31   
13   1.36944159368432   103.84648823913   700C       ANG MO KIO AVENUE 6   
14   1.36941049804616  103.846059822142   700B       ANG MO KIO AVENUE 6   
15   1.36476598625413  103.846907899709   316A      ANG MO KIO STREET 31   
16   1.36556100435159  103.845169497182   307C       ANG MO KIO AVENUE 1   
17   1.38198270653355  103.881217675808   984A             BUANGKOK LINK   
18   1.37946759731567  103.877266477065   988A            BUANGKOK GREEN   
19   1.38119524383438  103.880066273495   985A         BUANGKOK CRESCENT   
20   1.35025425918972  103.887795306397    165          HOUGANG AVENUE 1   
21   1.35160490053331  103.889848995071    169          HOUGANG AVENUE 1   
22   1.37499383603396  103.883486736367    917          HOUGANG AVENUE 9   
23   1.36987745772011  103.891412815739    838           HOUGANG CENTRAL   
24   1.37732845210703  103.904212191193   476B      UPPER SERANGOON VIEW   
25   1.37794957092139  103.904346035596   476C      UPPER SERANGOON VIEW   
26   1.37932250991171  103.904191032446   477C      UPPER SERANGOON VIEW   
27   1.38029686296144  103.877266407149   988C            BUANGKOK GREEN   
28   1.38001500314362  103.878741889941   978C         BUANGKOK CRESCENT   
29   1.37932814973617  103.877789198004   987C            BUANGKOK GREEN   
30   1.37881205219672  103.904229621366   477B      UPPER SERANGOON VIEW   
31   1.37893083811935  103.900988286293   470B  UPPER SERANGOON CRESCENT   
32   1.37518254401409  103.900405982824   475D  UPPER SERANGOON CRESCENT   
33    1.3759384508005  103.901084524846   473B  UPPER SERANGOON CRESCENT   
34   1.37905480016801  103.901927831856   470A  UPPER SERANGOON CRESCENT   
35   1.37629840280721  103.900220786851   475A  UPPER SERANGOON CRESCENT   
36   1.37395824754613  103.879695215818    939         HOUGANG STREET 92   
37   1.37752183749175  103.883813276017    915         HOUGANG STREET 91   
38   1.37607144536272  103.880924410023    926         HOUGANG STREET 91   
39   1.37893748878498  103.883857081014    911         HOUGANG STREET 91   
40   1.37972529696276  103.881133269191   980B         BUANGKOK CRESCENT   
41   1.37994979000929   103.89043869276    557         HOUGANG STREET 51   
42   1.36406322514465  103.893679750644   376C         HOUGANG STREET 32   
43   1.36346009799329  103.893576325679   376A         HOUGANG STREET 32   
44   1.37558451584826  103.883516297929    918          HOUGANG AVENUE 9   
45   1.37572957533559    103.8781874233    951          HOUGANG AVENUE 9   
46   1.37844987447131  103.891897726177    544          HOUGANG AVENUE 8   
47    1.3784780458325  103.895891713359    453         HOUGANG AVENUE 10   
48   1.35181593598792  103.888448131093    167          HOUGANG AVENUE 1   
49   1.35057934440742  103.889495942165    172          HOUGANG AVENUE 1   
50   1.37846690134355  103.900804189301   470C  UPPER SERANGOON CRESCENT   
51   1.37989436347789  103.877406233754   988B            BUA

In [26]:
list_of_lat = df_coordinates['latitude']
list_of_long = df_coordinates['longitude']
list_of_lat 


0       1.3785880768512
1      1.37175400663025
2      1.37243023974421
3      1.37197571261128
4      1.37193571932412
5      1.36548342757104
6      1.36598205054585
7      1.36583937026387
8      1.36406807879641
9      1.37205123278789
10     1.36432366673954
11     1.36421831526448
12     1.36502933267756
13     1.36944159368432
14     1.36941049804616
15     1.36476598625413
16     1.36556100435159
17     1.38198270653355
18     1.37946759731567
19     1.38119524383438
20     1.35025425918972
21     1.35160490053331
22     1.37499383603396
23     1.36987745772011
24     1.37732845210703
25     1.37794957092139
26     1.37932250991171
27     1.38029686296144
28     1.38001500314362
29     1.37932814973617
30     1.37881205219672
31     1.37893083811935
32     1.37518254401409
33      1.3759384508005
34     1.37905480016801
35     1.37629840280721
36     1.37395824754613
37     1.37752183749175
38     1.37607144536272
39     1.37893748878498
40     1.37972529696276
41     1.3799497

In [27]:
list_of_long

0      103.838639699065
1        103.8538833087
2      103.850949173949
3      103.853150894936
4       103.85014325987
5      103.844084739929
6       103.84444497466
7      103.844630828457
8      103.851612284582
9      103.850545847531
10     103.850307632579
11     103.846861474806
12     103.845300649183
13      103.84648823913
14     103.846059822142
15     103.846907899709
16     103.845169497182
17     103.881217675808
18     103.877266477065
19     103.880066273495
20     103.887795306397
21     103.889848995071
22     103.883486736367
23     103.891412815739
24     103.904212191193
25     103.904346035596
26     103.904191032446
27     103.877266407149
28     103.878741889941
29     103.877789198004
30     103.904229621366
31     103.900988286293
32     103.900405982824
33     103.901084524846
34     103.901927831856
35     103.900220786851
36     103.879695215818
37     103.883813276017
38     103.880924410023
39     103.883857081014
40     103.881133269191
41      103.8904

In [28]:
list_of_coordinates = []
for lat, long in zip(list_of_lat, list_of_long):
    list_of_coordinates.append((lat,long))

len(list_of_coordinates)

112

In [29]:
list_of_coordinates

[('1.3785880768512', '103.838639699065'),
 ('1.37175400663025', '103.8538833087'),
 ('1.37243023974421', '103.850949173949'),
 ('1.37197571261128', '103.853150894936'),
 ('1.37193571932412', '103.85014325987'),
 ('1.36548342757104', '103.844084739929'),
 ('1.36598205054585', '103.84444497466'),
 ('1.36583937026387', '103.844630828457'),
 ('1.36406807879641', '103.851612284582'),
 ('1.37205123278789', '103.850545847531'),
 ('1.36432366673954', '103.850307632579'),
 ('1.36421831526448', '103.846861474806'),
 ('1.36502933267756', '103.845300649183'),
 ('1.36944159368432', '103.84648823913'),
 ('1.36941049804616', '103.846059822142'),
 ('1.36476598625413', '103.846907899709'),
 ('1.36556100435159', '103.845169497182'),
 ('1.38198270653355', '103.881217675808'),
 ('1.37946759731567', '103.877266477065'),
 ('1.38119524383438', '103.880066273495'),
 ('1.35025425918972', '103.887795306397'),
 ('1.35160490053331', '103.889848995071'),
 ('1.37499383603396', '103.883486736367'),
 ('1.369877457720

In [30]:
df_filtered_sorted.shape

(183, 12)

In [31]:
df_coordinates.shape

(112, 6)

<h2>Combine  list_of_coordinates (Drop address Column ) Join by blk_no with block df_filtered_sorted </h2>

In [32]:
df_hdb_Coor = pd.merge(df_filtered_sorted,df_coordinates, how='left', left_on = 'block', right_on = 'blk_no')
# remove the "address" column
df_hdb_Coor.drop("address_x", axis=1, inplace=True)
df_hdb_Coor.drop("blk_no", axis=1, inplace=True)

df_hdb_Coor.head()


month        town flat_type block       street_name storey_range  \
0  2021-01  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     01 TO 03   
1  2021-04  ANG MO KIO    4 ROOM  588D  ANG MO KIO ST 52     16 TO 18   
2  2021-02  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     13 TO 15   
3  2021-02  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     22 TO 24   
4  2021-02  ANG MO KIO    4 ROOM  596C  ANG MO KIO ST 52     22 TO 24   

   floor_area_sqm flat_model  lease_commence_date  remain_lease  resale_price  \
0           107.0    Model A                 1996            74      508000.0   
1            91.0       DBSS                 2011            89      770000.0   
2            91.0    Model A                 2002            80      665000.0   
3            90.0       DBSS                 2011            89      768000.0   
4            90.0    Model A                 2002            80      680888.0   

           latitude         longitude             road_name postal_code  \
0   1.3785880768512  103.838639699065   ANG MO KIO AVENUE 4      560619   
1  1.37175400663025    103.8538833087  ANG MO KIO STREET 52      564588   
2  1.37243023974421  103.850949173949  ANG MO KIO STREET 52      561596   
3  1.37197571261128  103.853150894936  ANG MO KIO STREET 52      562588   
4  1.37193571932412   103.85014325987  ANG MO KIO STREET 52      563596   

               address_y  
0   619 ANG MO KIO AVE 4  
1  588D ANG MO KIO ST 52  
2  596A ANG MO KIO ST 52  
3  588B ANG MO KIO ST 52  
4  596C ANG MO KIO ST 52

<b>Rename Address Column from address_y to address</b>

In [33]:
df_hdb_Coor = df_hdb_Coor.rename(columns={'address_y': 'address'})
df_hdb_Coor


month        town flat_type block         street_name storey_range  \
0    2021-01  ANG MO KIO    4 ROOM   619    ANG MO KIO AVE 4     01 TO 03   
1    2021-04  ANG MO KIO    4 ROOM  588D    ANG MO KIO ST 52     16 TO 18   
2    2021-02  ANG MO KIO    4 ROOM  596A    ANG MO KIO ST 52     13 TO 15   
3    2021-02  ANG MO KIO    4 ROOM  588B    ANG MO KIO ST 52     22 TO 24   
4    2021-02  ANG MO KIO    4 ROOM  596C    ANG MO KIO ST 52     22 TO 24   
5    2021-02  ANG MO KIO    4 ROOM  308A    ANG MO KIO AVE 1     04 TO 06   
6    2021-03  ANG MO KIO    4 ROOM  307A    ANG MO KIO AVE 1     07 TO 09   
7    2021-03  ANG MO KIO    4 ROOM  307B    ANG MO KIO AVE 1     04 TO 06   
8    2021-03  ANG MO KIO    4 ROOM   619    ANG MO KIO AVE 4     10 TO 12   
9    2021-03  ANG MO KIO    4 ROOM   619    ANG MO KIO AVE 4     07 TO 09   
10   2021-03  ANG MO KIO    4 ROOM   353    ANG MO KIO ST 32     01 TO 03   
11   2021-03  ANG MO KIO    4 ROOM  588B    ANG MO KIO ST 52     01 TO 03   
12   2021-03  ANG MO KIO    4 ROOM  596B    ANG MO KIO ST 52     10 TO 12   
13   2021-03  ANG MO KIO    4 ROOM  588D    ANG MO KIO ST 52     13 TO 15   
14   2021-01  ANG MO KIO    4 ROOM  588B    ANG MO KIO ST 52     28 TO 30   
15   2021-01  ANG MO KIO    4 ROOM  596A    ANG MO KIO ST 52     04 TO 06   
16   2021-01  ANG MO KIO    4 ROOM   351    ANG MO KIO ST 32     19 TO 21   
17   2021-01  ANG MO KIO    4 ROOM  315A    ANG MO KIO ST 31     16 TO 18   
18   2021-01  ANG MO KIO    4 ROOM  309A    ANG MO KIO ST 31     04 TO 06   
19   2021-01  ANG MO KIO    4 ROOM  315A    ANG MO KIO ST 31     04 TO 06   
20   2021-01  ANG MO KIO    4 ROOM  700C    ANG MO KIO AVE 6     13 TO 15   
21   2021-01  ANG MO KIO    4 ROOM  700B    ANG MO KIO AVE 6     22 TO 24   
22   2021-04  ANG MO KIO    4 ROOM  316A    ANG MO KIO ST 31     16 TO 18   
23   2021-04  ANG MO KIO    4 ROOM  307C    ANG MO KIO AVE 1     07 TO 09   
24   2021-04     HOUGANG    4 ROOM  984A       BUANGKOK LINK     04 TO 06   
25   2021-04     HOUGANG    4 ROOM  988A      BUANGKOK GREEN     07 TO 09   
26   2021-03     HOUGANG    4 ROOM  985A       BUANGKOK CRES     10 TO 12   
27   2021-04     HOUGANG    4 ROOM   165       HOUGANG AVE 1     10 TO 12   
28   2021-04     HOUGANG    4 ROOM   169       HOUGANG AVE 1     10 TO 12   
29   2021-04     HOUGANG    4 ROOM   917       HOUGANG AVE 9     13 TO 15   
30   2021-04     HOUGANG    4 ROOM   838        HOUGANG CTRL     10 TO 12   
31   2021-02     HOUGANG    4 ROOM  476B  UPP SERANGOON VIEW     13 TO 15   
32   2021-02     HOUGANG    4 ROOM  476B  UPP SERANGOON VIEW     07 TO 09   
33   2021-02     HOUGANG    4 ROOM  476C  UPP SERANGOON VIEW     10 TO 12   
34   2021-02     HOUGANG    4 ROOM  476B  UPP SERANGOON VIEW     07 TO 09   
35   2021-02     HOUGANG    4 ROOM  477C  UPP SERANGOON VIEW     19 TO 21   
36   2021-04     HOUGANG    4 ROOM  988C      BUANGKOK GREEN     01 TO 03   
37   2021-03     HOUGANG    4 ROOM  978C       BUANGKOK CRES     10 TO 12   
38   2021-03     HOUGANG    4 ROOM  987C      BUANGKOK GREEN     01 TO 03   
39   2021-03     HOUGANG    4 ROOM  987C      BUANGKOK GREEN     10 TO 12   
40   2021-03     HOUGANG    4 ROOM  476B  UPP SERANGOON VIEW     16 TO 18   
41   2021-03     HOUGANG    4 ROOM  477B  UPP SERANGOON VIEW     07 TO 09   
42   2021-03     HOUGANG    4 ROOM  477B  UPP SERANGOON VIEW     13 TO 15   
43   2021-03     HOUGANG    4 ROOM  470B  UPP SERANGOON CRES     16 TO 18   
44   2021-03     HOUGANG    4 ROOM  475D  UPP SERANGOON CRES     16 TO 18   
45   2021-03     HOUGANG    4 ROOM  473B  UPP SERANGOON CRES     16 TO 18   
46   2021-03     HOUGANG    4 ROOM  470A  UPP SERANGOON CRES     04 TO 06   
47   2021-03     HOUGANG    4 ROOM  475A  UPP SERANGOON CRES     07 TO 09   
48   2021-03     HOUGANG    4 ROOM  473B  UPP SERANGOON CRES     10 TO 12   
49   2021-03     HOUGANG    4 ROOM   939       HOUGANG ST 92     07 TO 09   
50   2021-03     HOUGANG    4 ROOM   915       HOUGANG ST 91     07 TO 09   
51 

<H2>Next Step I need to Get the Coordinate of MRT ( Train Station)  And Then Compare the Train Station Location with the Flat Unit</H2>

In [34]:
#The CSV File copy form data.gov.sg 

url_1 = 'https://raw.githubusercontent.com/khaiseng82/mrt/main/mrt_lrt_data.csv'
df_mrt = pd.read_csv(url_1, index_col=0)

df_mrt

type       lat         lng
station_name                                
Jurong East        MRT  1.333207  103.742308
Bukit Batok        MRT  1.349069  103.749596
Bukit Gombak       MRT  1.359043  103.751863
Choa Chu Kang      MRT  1.385417  103.744316
Yew Tee            MRT  1.397383  103.747523
Kranji             MRT  1.425302  103.762049
Marsiling          MRT  1.432579  103.774150
Woodlands          MRT  1.436984  103.786406
Admiralty          MRT  1.436984  103.786406
Sembawang          MRT  1.449133  103.820060
Yishun             MRT  1.429666  103.835044
Khatib             MRT  1.417423  103.832995
Yio Chu Kang       MRT  1.381765  103.844923
Ang Mo Kio         MRT  1.370025  103.849588
Bishan             MRT  1.350920  103.848206
Braddell           MRT  1.340550  103.847098
Toa Payoh          MRT  1.332405  103.847436
Novena             MRT  1.320089  103.843405
Newton             MRT  1.313830  103.838021
Orchard            MRT  1.304041  103.831792
Somerset           MRT  1.300508  103.838428
Dhoby Ghaut        MRT  1.299169  103.845799
City Hall          MRT  1.293119  103.852089
Raffles Place      MRT  1.284001  103.851550
Marina Bay         MRT  1.276481  103.854598
Marina South Pier  MRT  1.271422  103.863581
Tuas Link          MRT  1.340371  103.636866
Tuas West Road     MRT  1.330075  103.639636
Tuas Crescent      MRT  1.321091  103.649075
Gul Circle         MRT  1.319809  103.660830
Joo Koon           MRT  1.327826  103.678318
Pioneer            MRT  1.337645  103.697420
Boon Lay           MRT  1.338620  103.705817
Lakeside           MRT  1.344264  103.720797
Chinese Garden     MRT  1.342436  103.732582
Clementi           MRT  1.314925  103.765341
Dover              MRT  1.311414  103.778596
Buona Vista        MRT  1.307337  103.790046
Commonwealth       MRT  1.302439  103.798326
Queenstown         MRT  1.294867  103.805902
Redhill            MRT  1.289674  103.816787
Tiong Bahru        MRT  1.286555  103.826956
Outram Park        MRT  1.280319  103.839459
Tanjong Pagar      MRT  1.276385  103.846771
Bugis              MRT  1.300747  103.855873
Lavender           MRT  1.307577  103.863155
Kallang            MRT  1.311532  103.871372
Aljunied           MRT  1.316474  103.882762
Paya Lebar         MRT  1.318214  103.893133
Eunos              MRT  1.319809  103.902888
Kembangan          MRT  1.320998  103.913433
Bedok              MRT  1.324043  103.930205
Tanah Merah        MRT  1.327309  103.946479
Simei              MRT  1.343237  103.953343
Tampines           MRT  1.354467  103.943325
Pasir Ris          MRT  1.373234  103.949343
Expo               MRT  1.334479  103.961459
Changi Airport     MRT  1.357622  103.988487
HarbourFront       MRT  1.265453  103.820514
Chinatown          MRT  1.284566  103.843626
Clarke Quay        MRT  1.288949  103.847521
Little India       MRT  1.306691  103.849396
Farrer Park        MRT  1.312679  103.854872
Boon Keng          MRT  1.320091  103.861655
Potong Pasir       MRT  1.331316  103.868779
Woodleigh          MRT  1.339202  103.870727
Serangoon          MRT  1.349862  103.873635
Kovan              MRT  1.360207  103.885163
Hougang            MRT  1.371406  103.892533
Buangkok           MRT  1.382991  103.893347
Sengkang           MRT  1.391682  103.895475
Punggol            MRT  1.405191  103.902367
Bras Basah         MRT  1.296978  103.850715
Esplanade          MRT  1.293995  103.855396
Promenade          MRT  1.294063  103.860156
Nicoll Highway     MRT  1.300292  103.863449
Stadium            MRT  1.302847  103.875417
Mountbatten        MRT  1.306106  103.883175
Dakota             MRT  1.308474  103.888825
MacPherson         MRT  1.326769  103.889901
Tai Seng           MRT  1.335940  103.887706
Bartley            MRT  1.342923  103.879660
Lorong Chuan       MRT  1.351530  103.864957
Marymount          MRT  1.349089  103.839116
Caldecott          MRT  1.337649  103.839627
Botanic Gardens    MRT  1.322387  103.814905
Farrer Road        MRT  1.317606  103.807711
Holland Villa

In [35]:
list_of_mrt_coordinates = []
mrt_lat = df_mrt['lat']
mrt_long = df_mrt['lng']

In [36]:
for lat, long in zip(mrt_lat, mrt_long):
    list_of_mrt_coordinates.append((lat, long))
    
len(list_of_mrt_coordinates)

157

<h2> List Of MRT Coordinates</h2>

list_of_mrt_coordinates

In [37]:
list_of_la = df_hdb_Coor ["latitude"].tolist()
list_of_lo = df_hdb_Coor ["longitude"].tolist()

In [38]:
list_of_coordinate=[]
temp =[]

for x, y in zip(list_of_la, list_of_lo ):
                
        temp=[x,y]
        list_of_coordinate.append(temp)   
temp.clear()
    
    
list_of_coordinate

[['1.3785880768512', '103.838639699065'],
 ['1.37175400663025', '103.8538833087'],
 ['1.37243023974421', '103.850949173949'],
 ['1.37197571261128', '103.853150894936'],
 ['1.37193571932412', '103.85014325987'],
 ['1.36548342757104', '103.844084739929'],
 ['1.36598205054585', '103.84444497466'],
 ['1.36583937026387', '103.844630828457'],
 ['1.3785880768512', '103.838639699065'],
 ['1.3785880768512', '103.838639699065'],
 ['1.36406807879641', '103.851612284582'],
 ['1.37197571261128', '103.853150894936'],
 ['1.37205123278789', '103.850545847531'],
 ['1.37175400663025', '103.8538833087'],
 ['1.37197571261128', '103.853150894936'],
 ['1.37243023974421', '103.850949173949'],
 ['1.36432366673954', '103.850307632579'],
 ['1.36421831526448', '103.846861474806'],
 ['1.36502933267756', '103.845300649183'],
 ['1.36421831526448', '103.846861474806'],
 ['1.36944159368432', '103.84648823913'],
 ['1.36941049804616', '103.846059822142'],
 ['1.36476598625413', '103.846907899709'],
 ['1.36556100435159',

In [39]:
len(list_of_coordinate)

189

In [40]:
from geopy.distance import geodesic

list_of_dist_mrt = []
min_dist_mrt = []

# list_of_coordinates -> Flat Unit Coordinates
# Loop Theough the Flat Coordinates
for origin in list_of_coordinate:
    # Loop Through All MRT Station in the List in -> "list_of_mrt_coordinates"
    for destination in range(0, len(list_of_mrt_coordinates)):
        #geodesic is a  Function -> is use to Calculate the Distance between The Flat Unit 
        list_of_dist_mrt.append(geodesic(origin,list_of_mrt_coordinates[destination]).meters)
        # Append the Result into (list_of_dist_mrt) with every Loop
        #Get the  min () Minimum Distance
    shortest = (min(list_of_dist_mrt))
    #After getting the Shortest Distance append to min_dist_mrt list
    min_dist_mrt.append(shortest)
    # Clear the List  list_of_dist_mrt loop again
    list_of_dist_mrt.clear()

In [41]:
min_dist_mrt

[782.5324575496927,
 514.8306095744726,
 306.0736916342701,
 451.38025278018864,
 220.12880408769516,
 792.0099256205582,
 726.2540809755077,
 720.1050737040086,
 782.5324575496927,
 782.5324575496927,
 696.144898869748,
 451.38025278018864,
 248.11590951597796,
 514.8306095744726,
 451.38025278018864,
 306.0736916342701,
 635.4909666096543,
 710.1605833357081,
 729.9276867835097,
 710.1605833357081,
 350.945863197253,
 398.4794949173613,
 653.544545292213,
 696.7363355789988,
 978.6652011178988,
 1393.9617517624163,
 1121.7940789692216,
 1138.845304711176,
 1084.756163359093,
 1082.0869801879924,
 210.01920753405437,
 767.7084028133728,
 767.7084028133728,
 707.4179940330537,
 767.7084028133728,
 560.0913653515806,
 1302.5849619644432,
 1313.9458233520543,
 1415.161618244273,
 1415.161618244273,
 767.7084028133728,
 613.7574853244953,
 613.7574853244953,
 570.8597186386244,
 970.5925038994925,
 894.6920904281399,
 542.6757818891539,
 873.9146437186615,
 894.6920904281399,
 1456.294992

<b>Append  Distance between MRT and Flat Unit List to  df_hdb_Coor Data Frame </b> 

In [42]:
len(min_dist_mrt)

189

Can Only Merge if Same length

In [43]:
df_hdb_Coor.shape


(189, 16)

In [44]:
df_hdb_Coor['min_dist_mrt'] = min_dist_mrt

<H2> Now We have  Achieve the Below , Next Step is to Use FourSquare API to Get NearBy Venues  ( Shopping Mall Coffee Shop, School)</h2>


        Filtered to 3 Area  ( Ang Mo Kio , Toa Payoh , Hougang )-> Done 
        Filtered to  4  Room -> Done 
        Calculate shortest Distance Between MRT Distance ->  Done 
        Filtered Lease Year Left more than 70 Years->  Done
        
        What's Left to be complete
       
        (1) Hyper Mart
        (2) Great Food
        (3) Property Price Below Average

    




In [45]:
df_hdb_Coor.head()

month        town flat_type block       street_name storey_range  \
0  2021-01  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     01 TO 03   
1  2021-04  ANG MO KIO    4 ROOM  588D  ANG MO KIO ST 52     16 TO 18   
2  2021-02  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     13 TO 15   
3  2021-02  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     22 TO 24   
4  2021-02  ANG MO KIO    4 ROOM  596C  ANG MO KIO ST 52     22 TO 24   

   floor_area_sqm flat_model  lease_commence_date  remain_lease  resale_price  \
0           107.0    Model A                 1996            74      508000.0   
1            91.0       DBSS                 2011            89      770000.0   
2            91.0    Model A                 2002            80      665000.0   
3            90.0       DBSS                 2011            89      768000.0   
4            90.0    Model A                 2002            80      680888.0   

           latitude         longitude             road_name postal_code  \
0   1.3785880768512  103.838639699065   ANG MO KIO AVENUE 4      560619   
1  1.37175400663025    103.8538833087  ANG MO KIO STREET 52      564588   
2  1.37243023974421  103.850949173949  ANG MO KIO STREET 52      561596   
3  1.37197571261128  103.853150894936  ANG MO KIO STREET 52      562588   
4  1.37193571932412   103.85014325987  ANG MO KIO STREET 52      563596   

                 address  min_dist_mrt  
0   619 ANG MO KIO AVE 4    782.532458  
1  588D ANG MO KIO ST 52    514.830610  
2  596A ANG MO KIO ST 52    306.073692  
3  588B ANG MO KIO ST 52    451.380253  
4  596C ANG MO KIO ST 52    220.128804

# I will Use Four Square To display Marker for all  184 Potential Flat  for my Client , the Number of Potential Flat will be reduce base on Condition Evaluation Later

<h2>Connect to Four Square API</h2>

In [61]:
CLIENT_ID = 'T15SDXVGR055HT5NGX0DTFW5CCDLVAW4GGUKJU1QTWOD4XPC' # your Foursquare ID
CLIENT_SECRET = 'HETI5PMYVBGXDNW2XG2KRIPD3EWA0MUNFQ3ZWUR1PZUGISRX' # your Foursquare Secret
ACCESS_TOKEN = 'GJ1BUBLBS02MW1PSGD0PJKTVDROECJCAPH2SAHL3LRXZSHBC' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: T15SDXVGR055HT5NGX0DTFW5CCDLVAW4GGUKJU1QTWOD4XPC
CLIENT_SECRET:HETI5PMYVBGXDNW2XG2KRIPD3EWA0MUNFQ3ZWUR1PZUGISRX


<h2>Add Marker</h2>

In [60]:
address = "singapore, ON"

geolocator = Nominatim(user_agent="singapore_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Singapore city are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Singapore city are 1.3356313, 103.8387167.


In [62]:
map_sg = folium.Map(location=[latitude, longitude], zoom_start=10)


In [63]:
for lat, lng in zip(
        df_hdb_Coor['latitude'], 
        df_hdb_Coor['longitude']): 
       
   
    folium.Marker(
        [lat, lng],
        radius=5,
       
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_sg)  

map_sg


# <h2>Get Near By Venue</h2>

In [64]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    venues_list=[]
    
    for name, lat, lng in zip(names, latitudes, longitudes):
        # print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [65]:

hdb_venues= getNearbyVenues(names='ang mo kio',
                                   latitudes=df_hdb_Coor['latitude'],
                                   longitudes=df_hdb_Coor['longitude']
                                  )

# Divide the Main Frame into 3 Separate Small Frame

Reason Of Dividing is the DataFrame Too Large for Four Square API to Load

# Toa Payoh Venue

In [66]:
df_tpy = df_hdb_Coor[df_hdb_Coor['town'].str.contains("TOA PAYOH")].reset_index(drop=True)

df_tpy

month       town flat_type block         street_name storey_range  \
0   2021-03  TOA PAYOH    4 ROOM  138C    LOR 1A TOA PAYOH     13 TO 15   
1   2021-03  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     37 TO 39   
2   2021-03  TOA PAYOH    4 ROOM   122     LOR 2 TOA PAYOH     10 TO 12   
3   2021-03  TOA PAYOH    4 ROOM  139B    LOR 1A TOA PAYOH     16 TO 18   
4   2021-04  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     22 TO 24   
5   2021-04  TOA PAYOH    4 ROOM   148  POTONG PASIR AVE 1     04 TO 06   
6   2021-04  TOA PAYOH    4 ROOM   146  POTONG PASIR AVE 1     01 TO 03   
7   2021-04  TOA PAYOH    4 ROOM   146  POTONG PASIR AVE 1     01 TO 03   
8   2021-03  TOA PAYOH    4 ROOM    84     LOR 2 TOA PAYOH     13 TO 15   
9   2021-03  TOA PAYOH    4 ROOM   152     LOR 2 TOA PAYOH     07 TO 09   
10  2021-03  TOA PAYOH    4 ROOM   145     LOR 2 TOA PAYOH     34 TO 36   
11  2021-03  TOA PAYOH    4 ROOM    36     LOR 5 TOA PAYOH     13 TO 15   
12  2021-03  TOA PAYOH    4 ROOM     6     LOR 7 TOA PAYOH     07 TO 09   
13  2021-03  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     31 TO 33   
14  2021-03  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     07 TO 09   
15  2021-03  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     22 TO 24   
16  2021-03  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     04 TO 06   
17  2021-03  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     10 TO 12   
18  2021-03  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     10 TO 12   
19  2021-04  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     31 TO 33   
20  2021-03  TOA PAYOH    4 ROOM  138B    LOR 1A TOA PAYOH     31 TO 33   
21  2021-02  TOA PAYOH    4 ROOM   148  POTONG PASIR AVE 1     01 TO 03   
22  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     07 TO 09   
23  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     04 TO 06   
24  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     04 TO 06   
25  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     13 TO 15   
26  2021-01  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     13 TO 15   
27  2021-01  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     13 TO 15   
28  2021-01  TOA PAYOH    4 ROOM   79D      TOA PAYOH CTRL     16 TO 18   
29  2021-01  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     25 TO 27   
30  2021-01  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     25 TO 27   
31  2021-01  TOA PAYOH    4 ROOM    11     LOR 8 TOA PAYOH     04 TO 06   
32  2021-01  TOA PAYOH    4 ROOM   10B     LOR 7 TOA PAYOH     07 TO 09   
33  2021-01  TOA PAYOH    4 ROOM    14     LOR 7 TOA PAYOH     13 TO 15   
34  2021-01  TOA PAYOH    4 ROOM     7     LOR 7 TOA PAYOH     04 TO 06   
35  2021-01  TOA PAYOH    4 ROOM     7     LOR 7 TOA PAYOH     04 TO 06   
36  2021-01  TOA PAYOH    4 ROOM   141     LOR 2 TOA PAYOH     13 TO 15   
37  2021-01  TOA PAYOH    4 ROOM   143     LOR 2 TOA PAYOH     16 TO 18   
38  2021-01  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     22 TO 24   
39  2021-01  TOA PAYOH    4 ROOM   156     LOR 1 TOA PAYOH     01 TO 03   
40  2021-02  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     25 TO 27   
41  2021-02  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     04 TO 06   
42  2021-02  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     28 TO 30   
43  2021-02  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     31 TO 33   
44  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     16 TO 18   
45  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     10 TO 12   
46  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     10 TO 12   
47  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     04 TO 06   
48  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     07 TO 09   
49  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     13 TO 15   
50  2021-02  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     28 TO 30   
51  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     07 TO 09   
52  2021-02  TOA PAYOH    4 ROO

In [67]:
hdb_venues_tpy= getNearbyVenues(names='toa payoh',
                                   latitudes=df_tpy['latitude'],
                                   longitudes=df_tpy['longitude']
                                  )

In [68]:
hdb_venues_tpy.head()

Neighborhood Neighborhood Latitude Neighborhood Longitude  \
0            t      1.33626413671063       103.844907413472   
1            t      1.33626413671063       103.844907413472   
2            t      1.33626413671063       103.844907413472   
3            t      1.33626413671063       103.844907413472   
4            t      1.33626413671063       103.844907413472   

                                  Venue  Venue Latitude  Venue Longitude  \
0                              Creamier        1.337754       103.843380   
1                         Uggli Muffins        1.338179       103.844616   
2  Toa Payoh Lor 1 Market & Food Centre        1.337999       103.844623   
3          Hup Chong Hakka Yong Dou Foo        1.338293       103.844422   
4             Hua Fong Kee Roasted Duck        1.338283       103.844420   

     Venue Category  
0    Ice Cream Shop  
1            Bakery  
2        Food Court  
3  Hakka Restaurant  
4         BBQ Joint

<h2> We Are Only Interested in the Toa Payoh SuperMarket Cateogory</h2>

In [69]:
hdb_venues_tpy_sp = hdb_venues_tpy[hdb_venues_tpy['Venue Category'].str.contains("Supermarket")].reset_index(drop=True)
hdb_venues_tpy_sp

Neighborhood Neighborhood Latitude Neighborhood Longitude           Venue  \
0            t      1.33626413671063       103.844907413472  NTUC FairPrice   
1            p      1.33279631135029       103.845588638625  NTUC FairPrice   
2            a      1.33270900444626       103.867989929028  NTUC FairPrice   
3            y      1.33180078265389       103.867242849282  NTUC FairPrice   
4            o      1.33466409464552       103.846451369821  NTUC FairPrice   
5            h      1.33522145763857       103.847653597573  NTUC FairPrice   

   Venue Latitude  Venue Longitude Venue Category  
0        1.332965       103.847317    Supermarket  
1        1.332965       103.847317    Supermarket  
2        1.331637       103.868364    Supermarket  
3        1.331637       103.868364    Supermarket  
4        1.332965       103.847317    Supermarket  
5        1.332965       103.847317    Supermarket

<H2> Toa Payoh  : Calculate Flat Distance to Supermarket (Get the Minimum Distance) </H2>

In [73]:
hdb_venues_tpy_la = hdb_venues_tpy ["Neighborhood Latitude"].tolist()
hdb_venues_tpy_lo = hdb_venues_tpy ["Neighborhood Longitude"].tolist()


list_of_tpy_sp=[]
temp_1 =[]

for x, y in zip(hdb_venues_tpy_la, hdb_venues_tpy_lo):
                
        temp_1=[x,y]
        list_of_tpy_sp.append(temp_1)   
temp_1.clear()
    
    


In [74]:
hdb_venues_tpym_la = df_tpy["latitude"].tolist()
hdb_venues_tpym_lo = df_tpy["longitude"].tolist()


list_of_tpy_m=[]
temp_2 =[]

for x, y in zip(hdb_venues_tpym_la, hdb_venues_tpym_lo):
                
        temp_2=[x,y]
        list_of_tpy_m.append(temp_2)   
temp_2.clear()
    
    


In [85]:
list_of_dist_sp_tpy = []
min_dist_sp_tpy = []


for origin_1 in list_of_tpy_m:
    
    for destination in range(0, len(list_of_tpy_sp)):
        #geodesic is a  Function -> is use to Calculate the Distance between The Flat Unit 
        list_of_dist_sp_tpy.append(geodesic(origin_1,list_of_tpy_sp[destination]).meters)
        
        
    shortest = (min(list_of_dist_sp_tpy))
   
    min_dist_sp_tpy.append(shortest)
  
    list_of_dist_sp_tpy.clear()
  

In [86]:
 len(min_dist_sp_tpy) 

64

In [81]:
df_tpy.shape

(64, 17)

<h2>Toa Payoh : Calculate Flat Distance to Supermarket</h2>

In [83]:
df_tpy['min_dist_market'] = min_dist_sp_tpy

In [84]:
df_tpy

month       town flat_type block         street_name storey_range  \
0   2021-03  TOA PAYOH    4 ROOM  138C    LOR 1A TOA PAYOH     13 TO 15   
1   2021-03  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     37 TO 39   
2   2021-03  TOA PAYOH    4 ROOM   122     LOR 2 TOA PAYOH     10 TO 12   
3   2021-03  TOA PAYOH    4 ROOM  139B    LOR 1A TOA PAYOH     16 TO 18   
4   2021-04  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     22 TO 24   
5   2021-04  TOA PAYOH    4 ROOM   148  POTONG PASIR AVE 1     04 TO 06   
6   2021-04  TOA PAYOH    4 ROOM   146  POTONG PASIR AVE 1     01 TO 03   
7   2021-04  TOA PAYOH    4 ROOM   146  POTONG PASIR AVE 1     01 TO 03   
8   2021-03  TOA PAYOH    4 ROOM    84     LOR 2 TOA PAYOH     13 TO 15   
9   2021-03  TOA PAYOH    4 ROOM   152     LOR 2 TOA PAYOH     07 TO 09   
10  2021-03  TOA PAYOH    4 ROOM   145     LOR 2 TOA PAYOH     34 TO 36   
11  2021-03  TOA PAYOH    4 ROOM    36     LOR 5 TOA PAYOH     13 TO 15   
12  2021-03  TOA PAYOH    4 ROOM     6     LOR 7 TOA PAYOH     07 TO 09   
13  2021-03  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     31 TO 33   
14  2021-03  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     07 TO 09   
15  2021-03  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     22 TO 24   
16  2021-03  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     04 TO 06   
17  2021-03  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     10 TO 12   
18  2021-03  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     10 TO 12   
19  2021-04  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     31 TO 33   
20  2021-03  TOA PAYOH    4 ROOM  138B    LOR 1A TOA PAYOH     31 TO 33   
21  2021-02  TOA PAYOH    4 ROOM   148  POTONG PASIR AVE 1     01 TO 03   
22  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     07 TO 09   
23  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     04 TO 06   
24  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     04 TO 06   
25  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     13 TO 15   
26  2021-01  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     13 TO 15   
27  2021-01  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     13 TO 15   
28  2021-01  TOA PAYOH    4 ROOM   79D      TOA PAYOH CTRL     16 TO 18   
29  2021-01  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     25 TO 27   
30  2021-01  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     25 TO 27   
31  2021-01  TOA PAYOH    4 ROOM    11     LOR 8 TOA PAYOH     04 TO 06   
32  2021-01  TOA PAYOH    4 ROOM   10B     LOR 7 TOA PAYOH     07 TO 09   
33  2021-01  TOA PAYOH    4 ROOM    14     LOR 7 TOA PAYOH     13 TO 15   
34  2021-01  TOA PAYOH    4 ROOM     7     LOR 7 TOA PAYOH     04 TO 06   
35  2021-01  TOA PAYOH    4 ROOM     7     LOR 7 TOA PAYOH     04 TO 06   
36  2021-01  TOA PAYOH    4 ROOM   141     LOR 2 TOA PAYOH     13 TO 15   
37  2021-01  TOA PAYOH    4 ROOM   143     LOR 2 TOA PAYOH     16 TO 18   
38  2021-01  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     22 TO 24   
39  2021-01  TOA PAYOH    4 ROOM   156     LOR 1 TOA PAYOH     01 TO 03   
40  2021-02  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     25 TO 27   
41  2021-02  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     04 TO 06   
42  2021-02  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     28 TO 30   
43  2021-02  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     31 TO 33   
44  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     16 TO 18   
45  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     10 TO 12   
46  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     10 TO 12   
47  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     04 TO 06   
48  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     07 TO 09   
49  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     13 TO 15   
50  2021-02  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     28 TO 30   
51  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     07 TO 09   
52  2021-02  TOA PAYOH    4 ROO

# Hougang Venue

In [87]:
df_hg = df_hdb_Coor[df_hdb_Coor['town'].str.contains("HOUGANG")].reset_index(drop=True)


In [88]:
hdb_venues_hg= getNearbyVenues(names='hougang',
                                   latitudes=df_hg['latitude'],
                                   longitudes=df_hg['longitude']
                                  )

In [89]:
hdb_venues_hg.head()

Neighborhood Neighborhood Latitude Neighborhood Longitude  \
0            h      1.38198270653355       103.881217675808   
1            h      1.38198270653355       103.881217675808   
2            h      1.38198270653355       103.881217675808   
3            h      1.38198270653355       103.881217675808   
4            h      1.38198270653355       103.881217675808   

                      Venue  Venue Latitude  Venue Longitude  \
0   Kampung Lorong Buangkok        1.383242       103.878222   
1                McDonald’s        1.384216       103.880951   
2  Bus Stop 66489 (Blk 969)        1.379076       103.879003   
3            Fitness Corner        1.378371       103.880273   
4            Bus Stop 67079        1.382573       103.876795   

         Venue Category  
0         Historic Site  
1  Fast Food Restaurant  
2              Bus Stop  
3  Gym / Fitness Center  
4           Bus Station

<h2> We Are Only Interested in the Hougang SuperMarket Cateogory</h2>

In [90]:
hdb_venues_hg_sp = hdb_venues_hg[hdb_venues_hg['Venue Category'].str.contains("Supermarket")].reset_index(drop=True)
hdb_venues_hg_sp

Neighborhood Neighborhood Latitude Neighborhood Longitude           Venue  \
0            n      1.37499383603396       103.883486736367  FairPrice Xtra   
1            g      1.36987745772011       103.891412815739  NTUC FairPrice   
2            g      1.36987745772011       103.891412815739  NTUC FairPrice   

   Venue Latitude  Venue Longitude Venue Category  
0        1.375279       103.879216    Supermarket  
1        1.371776       103.894068    Supermarket  
2        1.372699       103.893807    Supermarket

<h2>Hougang : Calculate Flat Distance to Supermarket (Get the Minimum Distance)</h2>

In [110]:
hdb_venues_hg_la = hdb_venues_hg ["Neighborhood Latitude"].tolist()
hdb_venues_hg_lo = hdb_venues_hg ["Neighborhood Longitude"].tolist()


list_of_hg_sp=[]
temp_3 =[]

for x, y in zip(hdb_venues_hg_la, hdb_venues_hg_lo):
                
        temp_3=[x,y]
        list_of_hg_sp.append(temp_3)   
temp_3.clear()
    


In [96]:
hdb_venues_hgm_la = df_hg["latitude"].tolist()
hdb_venues_hgm_lo = df_hg["longitude"].tolist()


list_of_hg_m=[]
temp_4 =[]

for x, y in zip(hdb_venues_hg_la, hdb_venues_hgm_lo):
                
        temp_4=[x,y]
        list_of_hg_m.append(temp_4)   
temp_4.clear()

    

In [98]:
list_of_dist_sp_hg = []
min_dist_sp_hg = []


for origin_2 in list_of_hg_m:
    
    for destination in range(0, len(list_of_hg_sp)):
        #geodesic is a  Function -> is use to Calculate the Distance between The Flat Unit 
        list_of_dist_sp_hg.append(geodesic(origin_2,list_of_hg_sp[destination]).meters)
        
        
    shortest = (min(list_of_dist_sp_hg))
   
    min_dist_sp_hg.append(shortest)
  
    list_of_dist_sp_hg.clear()
    

  

In [99]:
 len(min_dist_sp_hg) 

101

In [100]:
df_hg.shape

(101, 17)

In [101]:
df_hg['min_dist_market'] = min_dist_sp_hg

In [102]:
df_hg

month     town flat_type block         street_name storey_range  \
0    2021-04  HOUGANG    4 ROOM  984A       BUANGKOK LINK     04 TO 06   
1    2021-04  HOUGANG    4 ROOM  988A      BUANGKOK GREEN     07 TO 09   
2    2021-03  HOUGANG    4 ROOM  985A       BUANGKOK CRES     10 TO 12   
3    2021-04  HOUGANG    4 ROOM   165       HOUGANG AVE 1     10 TO 12   
4    2021-04  HOUGANG    4 ROOM   169       HOUGANG AVE 1     10 TO 12   
5    2021-04  HOUGANG    4 ROOM   917       HOUGANG AVE 9     13 TO 15   
6    2021-04  HOUGANG    4 ROOM   838        HOUGANG CTRL     10 TO 12   
7    2021-02  HOUGANG    4 ROOM  476B  UPP SERANGOON VIEW     13 TO 15   
8    2021-02  HOUGANG    4 ROOM  476B  UPP SERANGOON VIEW     07 TO 09   
9    2021-02  HOUGANG    4 ROOM  476C  UPP SERANGOON VIEW     10 TO 12   
10   2021-02  HOUGANG    4 ROOM  476B  UPP SERANGOON VIEW     07 TO 09   
11   2021-02  HOUGANG    4 ROOM  477C  UPP SERANGOON VIEW     19 TO 21   
12   2021-04  HOUGANG    4 ROOM  988C      BUANGKOK GREEN     01 TO 03   
13   2021-03  HOUGANG    4 ROOM  978C       BUANGKOK CRES     10 TO 12   
14   2021-03  HOUGANG    4 ROOM  987C      BUANGKOK GREEN     01 TO 03   
15   2021-03  HOUGANG    4 ROOM  987C      BUANGKOK GREEN     10 TO 12   
16   2021-03  HOUGANG    4 ROOM  476B  UPP SERANGOON VIEW     16 TO 18   
17   2021-03  HOUGANG    4 ROOM  477B  UPP SERANGOON VIEW     07 TO 09   
18   2021-03  HOUGANG    4 ROOM  477B  UPP SERANGOON VIEW     13 TO 15   
19   2021-03  HOUGANG    4 ROOM  470B  UPP SERANGOON CRES     16 TO 18   
20   2021-03  HOUGANG    4 ROOM  475D  UPP SERANGOON CRES     16 TO 18   
21   2021-03  HOUGANG    4 ROOM  473B  UPP SERANGOON CRES     16 TO 18   
22   2021-03  HOUGANG    4 ROOM  470A  UPP SERANGOON CRES     04 TO 06   
23   2021-03  HOUGANG    4 ROOM  475A  UPP SERANGOON CRES     07 TO 09   
24   2021-03  HOUGANG    4 ROOM  473B  UPP SERANGOON CRES     10 TO 12   
25   2021-03  HOUGANG    4 ROOM   939       HOUGANG ST 92     07 TO 09   
26   2021-03  HOUGANG    4 ROOM   915       HOUGANG ST 91     07 TO 09   
27   2021-03  HOUGANG    4 ROOM   926       HOUGANG ST 91     01 TO 03   
28   2021-03  HOUGANG    4 ROOM   911       HOUGANG ST 91     10 TO 12   
29   2021-03  HOUGANG    4 ROOM  980B       BUANGKOK CRES     04 TO 06   
30   2021-03  HOUGANG    4 ROOM   557       HOUGANG ST 51     04 TO 06   
31   2021-03  HOUGANG    4 ROOM  376C       HOUGANG ST 32     04 TO 06   
32   2021-03  HOUGANG    4 ROOM  376A       HOUGANG ST 32     10 TO 12   
33   2021-03  HOUGANG    4 ROOM  376A       HOUGANG ST 32     07 TO 09   
34   2021-03  HOUGANG    4 ROOM   918       HOUGANG AVE 9     04 TO 06   
35   2021-03  HOUGANG    4 ROOM   951       HOUGANG AVE 9     01 TO 03   
36   2021-03  HOUGANG    4 ROOM   544       HOUGANG AVE 8     07 TO 09   
37   2021-03  HOUGANG    4 ROOM   453      HOUGANG AVE 10     07 TO 09   
38   2021-03  HOUGANG    4 ROOM   167       HOUGANG AVE 1     04 TO 06   
39   2021-03  HOUGANG    4 ROOM   172       HOUGANG AVE 1     10 TO 12   
40   2021-03  HOUGANG    4 ROOM  984A       BUANGKOK LINK     07 TO 09   
41   2021-02  HOUGANG    4 ROOM  470C  UPP SERANGOON CRES     04 TO 06   
42   2021-03  HOUGANG    4 ROOM  988B      BUANGKOK GREEN     01 TO 03   
43   2021-03  HOUGANG    4 ROOM  988A      BUANGKOK GREEN     16 TO 18   
44   2021-03  HOUGANG    4 ROOM  376B       HOUGANG ST 32     10 TO 12   
45   2021-02  HOUGANG    4 ROOM  475D  UPP SERANGOON CRES     04 TO 06   
46   2021-02  HOUGANG    4 ROOM   926       HOUGANG ST 91     01 TO 03   
47   2021-04  HOUGANG    4 ROOM   548       HOUGANG ST 51     04 TO 06   
48   2021-04  HOUGANG    4 ROOM   909       HOUGANG ST 91     10 TO 12   
49   2021-04  HOUGANG    4 ROOM   970       HOUGANG ST 91     13 TO 15   
50   2021-04  HOUGANG    4 ROOM  470A  UPP SERANGOON CRES     07 TO 09   
51   2021-04  HOUGANG    4 ROOM  475C  UPP SERANGOON CRES     01 TO 03   
52   2021-04  HOUGANG    4 ROOM  475D  UPP SERANGOON CRES     16 TO 18   
53   2021-0

# Ang Mo Kio Venue

In [103]:
df_amk = df_hdb_Coor[df_hdb_Coor['town'].str.contains("ANG MO KIO")].reset_index(drop=True)

In [104]:
hdb_venues_amk= getNearbyVenues(names='ang mo kio',
                                   latitudes=df_amk['latitude'],
                                   longitudes=df_amk['longitude']
                                  )

In [105]:
hdb_venues_amk.head()

Neighborhood Neighborhood Latitude Neighborhood Longitude  \
0            a       1.3785880768512       103.838639699065   
1            a       1.3785880768512       103.838639699065   
2            a       1.3785880768512       103.838639699065   
3            a       1.3785880768512       103.838639699065   
4            a       1.3785880768512       103.838639699065   

                         Venue  Venue Latitude  Venue Longitude  \
0      香记粥 (Xiang Ji Porridge)        1.381202       103.840782   
1     Ho-Ree Roasted Food 好味烧腊        1.381160       103.840977   
2    Mr Teh Tarik Eating House        1.378301       103.836725   
3        Shanghai Ren Jia 上海人家        1.377068       103.841329   
4  Charcos The Flaming Chicken        1.378220       103.836871   

          Venue Category  
0     Chinese Restaurant  
1     Chinese Restaurant  
2             Food Court  
3    Shanghai Restaurant  
4  Australian Restaurant

 <h2> We Are Only Interested in Ang Mo Kio SuperMarket Cateogory</h2>

In [106]:
hdb_venues_amk_sp = hdb_venues_amk[hdb_venues_amk['Venue Category'].str.contains("Supermarket")].reset_index(drop=True)
hdb_venues_amk_sp 

Neighborhood Neighborhood Latitude Neighborhood Longitude           Venue  \
0            g      1.37243023974421       103.850949173949  FairPrice Xtra   
1            g      1.37243023974421       103.850949173949  NTUC FairPrice   
2            m      1.37193571932412        103.85014325987  FairPrice Xtra   
3            m      1.37193571932412        103.85014325987  NTUC FairPrice   
4            o      1.36548342757104       103.844084739929     Giant Super   
5                   1.36598205054585        103.84444497466     Giant Super   
6            k      1.36583937026387       103.844630828457     Giant Super   

   Venue Latitude  Venue Longitude Venue Category  
0        1.369279       103.848886    Supermarket  
1        1.371507       103.847082    Supermarket  
2        1.369279       103.848886    Supermarket  
3        1.371507       103.847082    Supermarket  
4        1.364839       103.847873    Supermarket  
5        1.364839       103.847873    Supermarket  
6        1.364839       103.847873    Supermarket

<h2>AMK : Calculate Flat Distance to Supermarket (Get the Minimum Distance)¶</h2>

In [108]:
hdb_venues_amk_la = hdb_venues_amk ["Neighborhood Latitude"].tolist()
hdb_venues_amk_lo = hdb_venues_amk ["Neighborhood Longitude"].tolist()


list_of_amk_sp=[]
temp_5 =[]

for x, y in zip(hdb_venues_amk_la, hdb_venues_amk_lo):
                
        temp_5=[x,y]
        list_of_amk_sp.append(temp_5)   
temp_5.clear()
    


In [112]:
hdb_venues_amkm_la = df_amk["latitude"].tolist()
hdb_venues_amkm_lo = df_amk["longitude"].tolist()


list_of_amk_m=[]
temp_6 =[]

for x, y in zip(hdb_venues_amkm_la, hdb_venues_amkm_lo):
                
        temp_6=[x,y]
        list_of_amk_m.append(temp_6)   
temp_6.clear()


In [114]:
list_of_dist_sp_amk = []
min_dist_sp_amk = []


for origin_3 in list_of_amk_m:
    
    for destination in range(0, len(list_of_amk_sp)):
        #geodesic is a  Function -> is use to Calculate the Distance between The Flat Unit 
        list_of_dist_sp_amk.append(geodesic(origin_3,list_of_amk_sp[destination]).meters)
        
        
    shortest = (min(list_of_dist_sp_amk))
   
    min_dist_sp_amk.append(shortest)
  
    list_of_dist_sp_amk.clear()
    
min_dist_sp_amk
    

[0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 801.2598817181639,
 0.0,
 46.58823601873189,
 0.0,
 0.0,
 0.0,
 653.6138409144354,
 306.194609388041,
 116.53078537341754,
 306.194609388041,
 445.01955344259085,
 419.54001229729425,
 279.82898049099344,
 0.0]

In [115]:
 len(min_dist_sp_amk) 

24

In [116]:
df_amk.shape

(24, 17)

In [117]:
df_amk['min_dist_market'] = min_dist_sp_amk

In [118]:
df_amk

month        town flat_type block       street_name storey_range  \
0   2021-01  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     01 TO 03   
1   2021-04  ANG MO KIO    4 ROOM  588D  ANG MO KIO ST 52     16 TO 18   
2   2021-02  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     13 TO 15   
3   2021-02  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     22 TO 24   
4   2021-02  ANG MO KIO    4 ROOM  596C  ANG MO KIO ST 52     22 TO 24   
5   2021-02  ANG MO KIO    4 ROOM  308A  ANG MO KIO AVE 1     04 TO 06   
6   2021-03  ANG MO KIO    4 ROOM  307A  ANG MO KIO AVE 1     07 TO 09   
7   2021-03  ANG MO KIO    4 ROOM  307B  ANG MO KIO AVE 1     04 TO 06   
8   2021-03  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     10 TO 12   
9   2021-03  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     07 TO 09   
10  2021-03  ANG MO KIO    4 ROOM   353  ANG MO KIO ST 32     01 TO 03   
11  2021-03  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     01 TO 03   
12  2021-03  ANG MO KIO    4 ROOM  596B  ANG MO KIO ST 52     10 TO 12   
13  2021-03  ANG MO KIO    4 ROOM  588D  ANG MO KIO ST 52     13 TO 15   
14  2021-01  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     28 TO 30   
15  2021-01  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     04 TO 06   
16  2021-01  ANG MO KIO    4 ROOM   351  ANG MO KIO ST 32     19 TO 21   
17  2021-01  ANG MO KIO    4 ROOM  315A  ANG MO KIO ST 31     16 TO 18   
18  2021-01  ANG MO KIO    4 ROOM  309A  ANG MO KIO ST 31     04 TO 06   
19  2021-01  ANG MO KIO    4 ROOM  315A  ANG MO KIO ST 31     04 TO 06   
20  2021-01  ANG MO KIO    4 ROOM  700C  ANG MO KIO AVE 6     13 TO 15   
21  2021-01  ANG MO KIO    4 ROOM  700B  ANG MO KIO AVE 6     22 TO 24   
22  2021-04  ANG MO KIO    4 ROOM  316A  ANG MO KIO ST 31     16 TO 18   
23  2021-04  ANG MO KIO    4 ROOM  307C  ANG MO KIO AVE 1     07 TO 09   

    floor_area_sqm flat_model  lease_commence_date  remain_lease  \
0            107.0    Model A                 1996            74   
1             91.0       DBSS                 2011            89   
2             91.0    Model A                 2002            80   
3             90.0       DBSS                 2011            89   
4             90.0    Model A                 2002            80   
5             94.0    Model A                 2012            90   
6             95.0    Model A                 2012            90   
7             88.0    Model A                 2012            90   
8            107.0    Model A                 1996            74   
9            107.0    Model A                 1996            74   
10            90.0    Model A                 2001            79   
11            90.0       DBSS                 2011            89   
12            91.0    Model A                 2002            80   
13            91.0       DBSS                 2011            89   
14            90.0       DBSS                 2011            89   
15            93.0    Model A                 2002            80   
16            95.0    Model A                 2001            79   
17            90.0    Model A                 2006            84   
18            90.0    Model A                 2006            84   
19            90.0    Model A                 2006            84   
20            85.0    Model A                 2003            81   
21            90.0    Model A                 2003            81   
22            95.0    Model A                 2006            84   
23            88.0    Model A                 2012            90   

    resale_price          latitude         longitude             road_name  \
0       508000.0   1.3785880768512  103.838639699065   ANG MO KIO AVENUE 4   
1       770000.0  1.37175400663025    103.8538833087  ANG MO KIO STREET 52   
2       665000.0  1.37243023974421  103.850949173949  ANG MO KIO STREET 52   
3       768000.0  1.37197571261128  103.853150894936  ANG MO KIO STREET 52   
4       680888.0  1.37193571932412   103.85014325987  ANG MO KIO

# Now We Have Completed All Data For AMK/ Toa Payoh/ Now We Need to Calculate the MEAN  Resale Price For different Flat Model

<H2>AMK :Calculate Average Resale Price By Flat_Type </H2>

In [119]:
df_amk_m=df_amk.groupby('flat_model', as_index=False)['resale_price'].mean()

In [120]:
df_amk_m

flat_model  resale_price
0       DBSS      741600.0
1    Model A      616849.0

<H2>Toa Payoh :Calculate Average Resale Price By Flat_Type </H2>

In [122]:
df_tpy_m=df_tpy.groupby('flat_model', as_index=False)['resale_price'].mean()
df_tpy_m

flat_model   resale_price
0        DBSS  822155.428571
1     Model A  687825.962264
2  Simplified  547500.000000

<H2>Hougang :Calculate Average Resale Price By Flat_Type </H2>

In [123]:
df_hg_m=df_hg.groupby('flat_model', as_index=False)['resale_price'].mean()
df_hg_m

flat_model   resale_price
0               DBSS  599841.142857
1            Model A  439658.888889
2           Model A2  399777.777778
3  Premium Apartment  551076.923077

# Now we got all Data is time to Select the Best Unit from Each Area  For My Client Mr Edwin to Decide which to Buy

    Recap Client Requiremnet
    Filtered to 3 Area  ( Ang Mo Kio , Toa Payoh , Hougang )-> Done 
    Filtered to  4  Room -> Done 
    Calculate shortest Distance Between MRT Distance ->  Done 
    Filtered Lease Year Left more than 70 Years->  Done

   
    
    Hyper Mart-> Done 

    Property Price Below Average-> Done 
    
    
    

# Toa Payoh 

In [139]:
df_tpy_lowest=df_tpy.sort_values(by='resale_price', ascending=True)
df_tpy_lowest

month       town flat_type block         street_name storey_range  \
16  2021-03  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     04 TO 06   
7   2021-04  TOA PAYOH    4 ROOM   146  POTONG PASIR AVE 1     01 TO 03   
6   2021-04  TOA PAYOH    4 ROOM   146  POTONG PASIR AVE 1     01 TO 03   
21  2021-02  TOA PAYOH    4 ROOM   148  POTONG PASIR AVE 1     01 TO 03   
34  2021-01  TOA PAYOH    4 ROOM     7     LOR 7 TOA PAYOH     04 TO 06   
35  2021-01  TOA PAYOH    4 ROOM     7     LOR 7 TOA PAYOH     04 TO 06   
39  2021-01  TOA PAYOH    4 ROOM   156     LOR 1 TOA PAYOH     01 TO 03   
31  2021-01  TOA PAYOH    4 ROOM    11     LOR 8 TOA PAYOH     04 TO 06   
57  2021-02  TOA PAYOH    4 ROOM   147     LOR 2 TOA PAYOH     01 TO 03   
12  2021-03  TOA PAYOH    4 ROOM     6     LOR 7 TOA PAYOH     07 TO 09   
5   2021-04  TOA PAYOH    4 ROOM   148  POTONG PASIR AVE 1     04 TO 06   
32  2021-01  TOA PAYOH    4 ROOM   10B     LOR 7 TOA PAYOH     07 TO 09   
33  2021-01  TOA PAYOH    4 ROOM    14     LOR 7 TOA PAYOH     13 TO 15   
41  2021-02  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     04 TO 06   
36  2021-01  TOA PAYOH    4 ROOM   141     LOR 2 TOA PAYOH     13 TO 15   
24  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     04 TO 06   
58  2021-02  TOA PAYOH    4 ROOM   84B     LOR 2 TOA PAYOH     01 TO 03   
23  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     04 TO 06   
37  2021-01  TOA PAYOH    4 ROOM   143     LOR 2 TOA PAYOH     16 TO 18   
2   2021-03  TOA PAYOH    4 ROOM   122     LOR 2 TOA PAYOH     10 TO 12   
46  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     10 TO 12   
30  2021-01  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     25 TO 27   
40  2021-02  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     25 TO 27   
22  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     07 TO 09   
51  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     07 TO 09   
8   2021-03  TOA PAYOH    4 ROOM    84     LOR 2 TOA PAYOH     13 TO 15   
62  2021-04  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     04 TO 06   
63  2021-04  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     04 TO 06   
18  2021-03  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     10 TO 12   
17  2021-03  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     10 TO 12   
11  2021-03  TOA PAYOH    4 ROOM    36     LOR 5 TOA PAYOH     13 TO 15   
29  2021-01  TOA PAYOH    4 ROOM   79A      TOA PAYOH CTRL     25 TO 27   
26  2021-01  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     13 TO 15   
25  2021-02  TOA PAYOH    4 ROOM     9         JOO SENG RD     13 TO 15   
27  2021-01  TOA PAYOH    4 ROOM     7   UPP ALJUNIED LANE     13 TO 15   
19  2021-04  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     31 TO 33   
45  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     10 TO 12   
47  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     04 TO 06   
55  2021-02  TOA PAYOH    4 ROOM   82A     LOR 4 TOA PAYOH     07 TO 09   
56  2021-02  TOA PAYOH    4 ROOM   81B     LOR 4 TOA PAYOH     22 TO 24   
44  2021-03  TOA PAYOH    4 ROOM     9         JOO SENG RD     16 TO 18   
9   2021-03  TOA PAYOH    4 ROOM   152     LOR 2 TOA PAYOH     07 TO 09   
52  2021-02  TOA PAYOH    4 ROOM   79C      TOA PAYOH CTRL     16 TO 18   
54  2021-04  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     34 TO 36   
48  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     07 TO 09   
4   2021-04  TOA PAYOH    4 ROOM   155     LOR 1 TOA PAYOH     22 TO 24   
61  2021-02  TOA PAYOH    4 ROOM   79B      TOA PAYOH CTRL     16 TO 18   
38  2021-01  TOA PAYOH    4 ROOM  139A    LOR 1A TOA PAYOH     22 TO 24   
14  2021-03  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     07 TO 09   
28  2021-01  TOA PAYOH    4 ROOM   79D      TOA PAYOH CTRL     16 TO 18   
53  2021-02  TOA PAYOH    4 ROOM   79C      TOA PAYOH CTRL     16 TO 18   
15  2021-03  TOA PAYOH    4 ROOM   79E      TOA PAYOH CTRL     22 TO 24   
59  2021-02  TOA PAYOH    4 ROO

In [127]:
df_tpy_lowest=df_tpy_lowest.iloc[[0]]
df_tpy_lowest

month       town flat_type block     street_name storey_range  \
16  2021-03  TOA PAYOH    4 ROOM   79A  TOA PAYOH CTRL     04 TO 06   

    floor_area_sqm flat_model  lease_commence_date  remain_lease  \
16            76.0    Model A                 2009            87   

    resale_price          latitude         longitude          road_name  \
16      520000.0  1.33453129537676  103.847565695822  TOA PAYOH CENTRAL   

   postal_code             address  min_dist_mrt  min_dist_market  
16      311079  79A TOA PAYOH CTRL    235.557481        76.939051

Calculate Lease Cost Per Year

In [133]:
oneyear_lease_cost = 520000/87
full_lease = oneyear_lease_cost *99
full_lease

591724.1379310344

<h2> Find the Lowest Flat Price near MRT & MArket</h2>

In [128]:
df_tpy_low_mrt=df_tpy.sort_values(by='min_dist_mrt', ascending=True)

In [130]:
df_tpy_low_mrt=df_tpy_low_mrt.iloc[[4]]
df_tpy_low_mrt

month       town flat_type block         street_name storey_range  \
6  2021-04  TOA PAYOH    4 ROOM   146  POTONG PASIR AVE 1     01 TO 03   

   floor_area_sqm  flat_model  lease_commence_date  remain_lease  \
6            93.0  Simplified                 1998            76   

   resale_price          latitude         longitude              road_name  \
6      535000.0  1.33180078265389  103.867242849282  POTONG PASIR AVENUE 1   

  postal_code                 address  min_dist_mrt  min_dist_market  
6      350146  146 POTONG PASIR AVE 1      179.1647              0.0

In [134]:
oneyear_lease_cost_1 = 535000/76
full_lease_1 = oneyear_lease_cost_1 *99
full_lease_1

696907.8947368421

<h2> Toa Payoh Summary : Base on the Result I would Recommend Block 79 A to My Client </h2>
    Reason : (1)Cheapest Resale Price
        
             (2)Distance  to MRT Not the Nearest but within the Top 5
            
             (3)Distance to Market Not the Nearest but within the Top 5
            
             (4) LeaseCOst per Year  is Cheaper 
                

# Ang Mo Kio

In [136]:
df_amk_lowest=df_amk.sort_values(by='resale_price', ascending=True)
df_amk_lowest

month        town flat_type block       street_name storey_range  \
18  2021-01  ANG MO KIO    4 ROOM  309A  ANG MO KIO ST 31     04 TO 06   
0   2021-01  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     01 TO 03   
9   2021-03  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     07 TO 09   
10  2021-03  ANG MO KIO    4 ROOM   353  ANG MO KIO ST 32     01 TO 03   
8   2021-03  ANG MO KIO    4 ROOM   619  ANG MO KIO AVE 4     10 TO 12   
19  2021-01  ANG MO KIO    4 ROOM  315A  ANG MO KIO ST 31     04 TO 06   
15  2021-01  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     04 TO 06   
17  2021-01  ANG MO KIO    4 ROOM  315A  ANG MO KIO ST 31     16 TO 18   
12  2021-03  ANG MO KIO    4 ROOM  596B  ANG MO KIO ST 52     10 TO 12   
22  2021-04  ANG MO KIO    4 ROOM  316A  ANG MO KIO ST 31     16 TO 18   
5   2021-02  ANG MO KIO    4 ROOM  308A  ANG MO KIO AVE 1     04 TO 06   
11  2021-03  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     01 TO 03   
2   2021-02  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     13 TO 15   
20  2021-01  ANG MO KIO    4 ROOM  700C  ANG MO KIO AVE 6     13 TO 15   
7   2021-03  ANG MO KIO    4 ROOM  307B  ANG MO KIO AVE 1     04 TO 06   
16  2021-01  ANG MO KIO    4 ROOM   351  ANG MO KIO ST 32     19 TO 21   
23  2021-04  ANG MO KIO    4 ROOM  307C  ANG MO KIO AVE 1     07 TO 09   
4   2021-02  ANG MO KIO    4 ROOM  596C  ANG MO KIO ST 52     22 TO 24   
6   2021-03  ANG MO KIO    4 ROOM  307A  ANG MO KIO AVE 1     07 TO 09   
21  2021-01  ANG MO KIO    4 ROOM  700B  ANG MO KIO AVE 6     22 TO 24   
14  2021-01  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     28 TO 30   
13  2021-03  ANG MO KIO    4 ROOM  588D  ANG MO KIO ST 52     13 TO 15   
3   2021-02  ANG MO KIO    4 ROOM  588B  ANG MO KIO ST 52     22 TO 24   
1   2021-04  ANG MO KIO    4 ROOM  588D  ANG MO KIO ST 52     16 TO 18   

    floor_area_sqm flat_model  lease_commence_date  remain_lease  \
18            90.0    Model A                 2006            84   
0            107.0    Model A                 1996            74   
9            107.0    Model A                 1996            74   
10            90.0    Model A                 2001            79   
8            107.0    Model A                 1996            74   
19            90.0    Model A                 2006            84   
15            93.0    Model A                 2002            80   
17            90.0    Model A                 2006            84   
12            91.0    Model A                 2002            80   
22            95.0    Model A                 2006            84   
5             94.0    Model A                 2012            90   
11            90.0       DBSS                 2011            89   
2             91.0    Model A                 2002            80   
20            85.0    Model A                 2003            81   
7             88.0    Model A                 2012            90   
16            95.0    Model A                 2001            79   
23            88.0    Model A                 2012            90   
4             90.0    Model A                 2002            80   
6             95.0    Model A                 2012            90   
21            90.0    Model A                 2003            81   
14            90.0       DBSS                 2011            89   
13            91.0       DBSS                 2011            89   
3             90.0       DBSS                 2011            89   
1             91.0       DBSS                 2011            89   

    resale_price          latitude         longitude             road_name  \
18      505055.0  1.36502933267756  103.845300649183  ANG MO KIO STREET 31   
0       508000.0   1.3785880768512  103.838639699065   ANG MO KIO AVENUE 4   
9       520000.0   1.3785880768512  103.838639699065   ANG MO KIO AVENUE 4   
10      520000.0  1.36406807879641  103.851612284582  ANG MO KIO STREET 32   
8       560000.0   1.3785880768512  103.838639699065   ANG MO KI

In [137]:
df_amk_lowest=df_amk_lowest.iloc[[6]]
df_amk_lowest

month        town flat_type block       street_name storey_range  \
15  2021-01  ANG MO KIO    4 ROOM  596A  ANG MO KIO ST 52     04 TO 06   

    floor_area_sqm flat_model  lease_commence_date  remain_lease  \
15            93.0    Model A                 2002            80   

    resale_price          latitude         longitude             road_name  \
15      583000.0  1.37243023974421  103.850949173949  ANG MO KIO STREET 52   

   postal_code                address  min_dist_mrt  min_dist_market  
15      561596  596A ANG MO KIO ST 52    306.073692              0.0

<h2> AMK Summary : Base on the Result I would Recommend Block 596 A to My Client </h2>
    Reason : (1)Cheapest Resale Price
        
             (2)Distance  to MRT Not the Nearest but within the Top 5
            
             (3)Distance to Market Not the Nearest but within the Top 5
            
           
                

# Hougang

In [140]:
df_hg_lowest=df_hg.sort_values(by='resale_price', ascending=True)
df_hg_lowest

month     town flat_type block         street_name storey_range  \
97   2021-01  HOUGANG    4 ROOM  984A       BUANGKOK LINK     01 TO 03   
68   2021-01  HOUGANG    4 ROOM   941       HOUGANG ST 92     01 TO 03   
73   2021-04  HOUGANG    4 ROOM   911       HOUGANG ST 91     04 TO 06   
46   2021-02  HOUGANG    4 ROOM   926       HOUGANG ST 91     01 TO 03   
29   2021-03  HOUGANG    4 ROOM  980B       BUANGKOK CRES     04 TO 06   
87   2021-02  HOUGANG    4 ROOM   964       HOUGANG AVE 9     01 TO 03   
0    2021-04  HOUGANG    4 ROOM  984A       BUANGKOK LINK     04 TO 06   
40   2021-03  HOUGANG    4 ROOM  984A       BUANGKOK LINK     07 TO 09   
55   2021-01  HOUGANG    4 ROOM   963       HOUGANG AVE 9     13 TO 15   
96   2021-01  HOUGANG    4 ROOM  984A       BUANGKOK LINK     16 TO 18   
34   2021-03  HOUGANG    4 ROOM   918       HOUGANG AVE 9     04 TO 06   
27   2021-03  HOUGANG    4 ROOM   926       HOUGANG ST 91     01 TO 03   
79   2021-02  HOUGANG    4 ROOM   556       HOUGANG ST 51     07 TO 09   
78   2021-02  HOUGANG    4 ROOM   555       HOUGANG ST 51     04 TO 06   
5    2021-04  HOUGANG    4 ROOM   917       HOUGANG AVE 9     13 TO 15   
76   2021-01  HOUGANG    4 ROOM   580       HOUGANG AVE 4     01 TO 03   
84   2021-02  HOUGANG    4 ROOM   965       HOUGANG AVE 9     07 TO 09   
70   2021-01  HOUGANG    4 ROOM  699B       HOUGANG ST 52     01 TO 03   
94   2021-01  HOUGANG    4 ROOM  980C       BUANGKOK CRES     07 TO 09   
69   2021-01  HOUGANG    4 ROOM   931       HOUGANG ST 91     04 TO 06   
26   2021-03  HOUGANG    4 ROOM   915       HOUGANG ST 91     07 TO 09   
42   2021-03  HOUGANG    4 ROOM  988B      BUANGKOK GREEN     01 TO 03   
13   2021-03  HOUGANG    4 ROOM  978C       BUANGKOK CRES     10 TO 12   
35   2021-03  HOUGANG    4 ROOM   951       HOUGANG AVE 9     01 TO 03   
71   2021-01  HOUGANG    4 ROOM   555       HOUGANG ST 51     01 TO 03   
38   2021-03  HOUGANG    4 ROOM   167       HOUGANG AVE 1     04 TO 06   
100  2021-02  HOUGANG    4 ROOM   169       HOUGANG AVE 1     04 TO 06   
72   2021-01  HOUGANG    4 ROOM   548       HOUGANG ST 51     07 TO 09   
22   2021-03  HOUGANG    4 ROOM  470A  UPP SERANGOON CRES     04 TO 06   
88   2021-02  HOUGANG    4 ROOM   954       HOUGANG AVE 9     10 TO 12   
30   2021-03  HOUGANG    4 ROOM   557       HOUGANG ST 51     04 TO 06   
25   2021-03  HOUGANG    4 ROOM   939       HOUGANG ST 92     07 TO 09   
14   2021-03  HOUGANG    4 ROOM  987C      BUANGKOK GREEN     01 TO 03   
89   2021-01  HOUGANG    4 ROOM   549       HOUGANG ST 51     07 TO 09   
37   2021-03  HOUGANG    4 ROOM   453      HOUGANG AVE 10     07 TO 09   
49   2021-04  HOUGANG    4 ROOM   970       HOUGANG ST 91     13 TO 15   
80   2021-02  HOUGANG    4 ROOM   557       HOUGANG ST 51     07 TO 09   
4    2021-04  HOUGANG    4 ROOM   169       HOUGANG AVE 1     10 TO 12   
90   2021-02  HOUGANG    4 ROOM   169       HOUGANG AVE 1     07 TO 09   
74   2021-04  HOUGANG    4 ROOM   566       HOUGANG ST 51     04 TO 06   
77   2021-02  HOUGANG    4 ROOM  699B       HOUGANG ST 52     04 TO 06   
86   2021-02  HOUGANG    4 ROOM   951       HOUGANG AVE 9     13 TO 15   
12   2021-04  HOUGANG    4 ROOM  988C      BUANGKOK GREEN     01 TO 03   
48   2021-04  HOUGANG    4 ROOM   909       HOUGANG ST 91     10 TO 12   
98   2021-01  HOUGANG    4 ROOM   167       HOUGANG AVE 1     07 TO 09   
2    2021-03  HOUGANG    4 ROOM  985A       BUANGKOK CRES     10 TO 12   
99   2021-01  HOUGANG    4 ROOM   453      HOUGANG AVE 10     10 TO 12   
39   2021-03  HOUGANG    4 ROOM   172       HOUGANG AVE 1     10 TO 12   
3    2021-04  HOUGANG    4 ROOM   165       HOUGANG AVE 1     10 TO 12   
85   2021-02  HOUGANG    4 ROOM   952       HOUGANG AVE 9     16 TO 18   
47   2021-04  HOUGANG    4 ROOM   548       HOUGANG ST 51     04 TO 06   
15   2021-03  HOUGANG    4 ROOM  987C      BUANGKOK GREEN     10 TO 12   
28   2021-03  HOUGANG    4 ROOM   911       HOUGANG ST 91     10 TO 12   
1    2021-0

In [141]:
df_hg_lowest.shape

(101, 18)

In [142]:
df_hg_lowest=df_hg_lowest.iloc[[95]]

In [143]:
df_hg_lowest

month     town flat_type block    street_name storey_range  \
75  2021-01  HOUGANG    4 ROOM   220  HOUGANG ST 21     13 TO 15   

    floor_area_sqm flat_model  lease_commence_date  remain_lease  \
75           104.0    Model A                 1992            70   

    resale_price          latitude         longitude          road_name  \
75      590000.0  1.35693439635219  103.884512515118  HOUGANG STREET 21   

   postal_code            address  min_dist_mrt  min_dist_market  
75      530220  220 HOUGANG ST 21     369.03772       114.156508

<h2> Hougang Summary : Base on Observation to the Table I would Recommend Block 220 A to My Client </h2>
    Reason : (1)Cheapest Resale Price
        
             (2)Distance  to MRT Not the Nearest but within the Top 5
            
             (3)Distance to Market Not the Nearest but within the Top 5
            
           
                